## About This Notebook

This notebook is designed to process and analyze electricity demand, carbon intensity, energy generation mix, weather data, and price data for the UK. It includes data cleaning, feature engineering, and merging of datasets to create a comprehensive dataset for further analysis and modeling. The workflow is structured into the following sections:

1. **Electricity Demand**: Processing and cleaning electricity demand data, including adjustments for daylight saving time and adding holiday information.  
2. **Carbon Intensity and Generation Mix**: Analyzing the carbon intensity and energy generation mix, including rolling and lag features.  
3. **Weather Data**: Integrating weather data to understand its impact on electricity demand and generation.  
4. **Data Merging**: Combining all datasets into a unified format for analysis and modeling.  

This notebook provides a detailed step-by-step approach to prepare the data for energy-related studies and predictive modeling.

## 📊 Data Required for the Project

| **Category**                     | **Features**                                                                                     | **Included** |
|-----------------------------------|--------------------------------------------------------------------------------------------------|--------------|
| ⚡ **Electricity Demand & Time Features** | Electricity Demand, Day, Month, Hour, Year, Day of Week, Is Holiday                              | ✅            |
| 🌤️ **Weather Features**           | Temperature, Solar Radiation, Wind Speed, Cloud Coverage                                         | ✅            |
| ♻️ **Carbon Intensity & Energy Mix** | % of Energy from Renewables, Low Carbon, Zero Carbon and Renewables, Total Generated, Generation by Source, Carbon Intensity | ✅            |



In [1]:
#from google.colab import drive
#drive.mount('/content/drive')

In [2]:
# Standart libraries
import os
import glob

# Third-party libraries
import pandas as pd

# Enable auto-reload for modules during development
%load_ext autoreload
%autoreload 2

pd.set_option('display.max_columns', None)

In [3]:
# Local libraries

import sys
sys.path.append('/content/drive/MyDrive/final_project/utils')

import data_cleaning as dc
import data_check as ck

#from utils import data_check as ck
#from utils import data_cleaning as dc

In [4]:
#file_path = "../data"
file_path = "/content/drive/MyDrive/final_project/data"

ml_path = os.path.join(file_path, "data_for_ml")

### Electricity Demand

In [5]:
demand_path = os.path.join(file_path, "electricity_demand")

#### UK

In [6]:
# Exploring the data
uk_demand_path = os.path.join(demand_path, "uk")

In [7]:
# Read the files in the directory
file_list = glob.glob(os.path.join(uk_demand_path, 'demanddata_*.csv'))

# Initialize an empty dictionary to store the dataframes
uk_demand = {}

# Loop through the files and read them into a dictionary
for file in file_list:

    # Get the file name with the path
    file_name = os.path.basename(file)

    # Extract the year from the file name
    year = file_name.split('_')[1].split('.')[0]

    # Read the file
    df = pd.read_csv(file)
    uk_demand[year] = df

    print(f'demanddata_{year} loaded')


demanddata_2025 loaded
demanddata_2023 loaded
demanddata_2019 loaded
demanddata_2021 loaded
demanddata_2022 loaded
demanddata_2024 loaded
demanddata_2020 loaded


In [8]:
uk_demand['2019'].head()

SETTLEMENT_DATE  SETTLEMENT_PERIOD     ND    TSD  ENGLAND_WALES_DEMAND  \
0     01-JAN-2019                  1  23808  25291                 22393   
1     01-JAN-2019                  2  24402  25720                 22962   
2     01-JAN-2019                  3  24147  25495                 22689   
3     01-JAN-2019                  4  23197  24590                 21849   
4     01-JAN-2019                  5  22316  24346                 20979   

   EMBEDDED_WIND_GENERATION  EMBEDDED_WIND_CAPACITY  \
0                      2912                    5918   
1                      2761                    5918   
2                      2709                    5918   
3                      2638                    5918   
4                      2557                    5918   

   EMBEDDED_SOLAR_GENERATION  EMBEDDED_SOLAR_CAPACITY  NON_BM_STOR  \
0                          0                    12663            0   
1                          0                    12663            0   
2                          0                    12663            0   
3                          0                    12663            0   
4                          0                    12663            0   

   PUMP_STORAGE_PUMPING  IFA_FLOW  IFA2_FLOW  BRITNED_FLOW  MOYLE_FLOW  \
0                   178      1553          0           176        -455   
1                    27      1554          0           194        -455   
2                    27      1505          0           581        -410   
3                    28      1503          0           600        -450   
4                   525      1503          0           675        -442   

   EAST_WEST_FLOW  NEMO_FLOW  NSL_FLOW  ELECLINK_FLOW  VIKING_FLOW  \
0            -250          0         0              0            0   
1            -236          0         0              0            0   
2            -311          0         0              0            0   
3            -315          0         0              0            0   
4            -463          0         0              0            0   

   GREENLINK_FLOW  
0               0  
1               0  
2               0  
3               0  
4               0

##### 📘 Columns Description

| **Column**                  | **Description**                                                                                                                                                                                                                   |
|-----------------------------|-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| **SETTLEMENT_DATE**         | The calendar date corresponding to the data.                                                                                                                                                                                     |
| **SETTLEMENT_PERIOD**       | Each day is divided into 48 half-hour periods. Some days may have 46 or 50 periods due to daylight saving changes.                                                                                                               |
| **ND (National Demand)**    | The total electricity demand across the entire UK (excluding some special cases).                                                                                                                                                |
| **TSD (Transmission System Demand)** | National Demand **plus** electricity used by: <ul><li>Power stations themselves (they need power to operate),</li><li>Pumped storage (pumping water uphill to store energy),</li><li>Exports to other countries via interconnectors.</li></ul> |
| **ENGLAND_WALES_DEMAND**    | Similar to ND, but only includes electricity demand in **England and Wales**, excluding Scotland and Northern Ireland.                                                                                                            |
| **EMBEDDED_WIND_GENERATION**| Estimated electricity generated by small, non-grid-connected wind farms. These farms reduce grid demand but are hard to measure directly — this is a modeled estimate.                                                           |
| **EMBEDDED_WIND_CAPACITY**  | Theoretical maximum electricity these small wind farms could generate under ideal wind conditions.                                                                                                                               |
| **EMBEDDED_SOLAR_GENERATION** | Estimated electricity generated by small, non-grid-connected solar panels. Like wind, this estimate helps model grid demand more accurately.                                                                                   |
| **EMBEDDED_SOLAR_CAPACITY** | The maximum output solar panels could produce under full sunlight.                                                                                                                                                              |
| **NON_BM_STOR**             | Electricity from reserves or generators not part of the main balancing mechanism. This includes: <ul><li>Extra capacity ready to dispatch,</li><li>Demand reduction agreements,</li><li>Acts as a backup to balance supply and demand.</li></ul> |
| **PUMPED_STORAGE_USAGE**    | Electricity used to **pump water uphill** in hydro storage plants (like charging a battery). Usually a **negative value**, as it represents electricity consumption for future generation.                                       |
| **Interconnector Flows**    | Cables connecting the UK grid to other countries. They allow for imports and exports of electricity. Includes: <ul><li>**IFA_FLOW** → France</li><li>**IFA2_FLOW** → France</li><li>**MOYLE_FLOW** → Northern Ireland</li><li>**EAST_WEST_FLOW** → Republic of Ireland</li><li>**NEMO_FLOW** → Belgium</li><li>**NSL_FLOW** → Norway (North Sea Link)</li><li>**BRITNED_FLOW** → Netherlands</li><li>**ELECLINK_FLOW** → France</li><li>**GREENLINK_FLOW** → Ireland</li></ul> <br>📌 *Positive values = Imports into the UK* <br>📌 *Negative values = Exports from the UK* |


In [9]:
# Snake case columns
for key, value in uk_demand.items():
    # Rename the columns
    uk_demand[key] = dc.snake(value)

In [10]:
uk_demand['2019'].head()

settlement_date  settlement_period     nd    tsd  england_wales_demand  \
0     01-JAN-2019                  1  23808  25291                 22393   
1     01-JAN-2019                  2  24402  25720                 22962   
2     01-JAN-2019                  3  24147  25495                 22689   
3     01-JAN-2019                  4  23197  24590                 21849   
4     01-JAN-2019                  5  22316  24346                 20979   

   embedded_wind_generation  embedded_wind_capacity  \
0                      2912                    5918   
1                      2761                    5918   
2                      2709                    5918   
3                      2638                    5918   
4                      2557                    5918   

   embedded_solar_generation  embedded_solar_capacity  non_bm_stor  \
0                          0                    12663            0   
1                          0                    12663            0   
2                          0                    12663            0   
3                          0                    12663            0   
4                          0                    12663            0   

   pump_storage_pumping  ifa_flow  ifa2_flow  britned_flow  moyle_flow  \
0                   178      1553          0           176        -455   
1                    27      1554          0           194        -455   
2                    27      1505          0           581        -410   
3                    28      1503          0           600        -450   
4                   525      1503          0           675        -442   

   east_west_flow  nemo_flow  nsl_flow  eleclink_flow  viking_flow  \
0            -250          0         0              0            0   
1            -236          0         0              0            0   
2            -311          0         0              0            0   
3            -315          0         0              0            0   
4            -463          0         0              0            0   

   greenlink_flow  
0               0  
1               0  
2               0  
3               0  
4               0

In [11]:
# Extracting necessary columns
uk_demand_clean = dc.extract_columns(uk_demand,["settlement_date", "settlement_period", "nd", "tsd"])

Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2025
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2023
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2019
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2021
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2022
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2024
Columns ['settlement_date', 'settlement_period', 'nd', 'tsd'] extracted from data 2020


In [12]:
# Check the 2019 data types, missing values, and duplicates
ck.check(uk_demand_clean['2019'])

Number of columns: 4 and rows: 17520

Data types:
settlement_date      object
settlement_period     int64
nd                    int64
tsd                   int64
dtype: object

Unique values count:
settlement_date        365
settlement_period       50
nd                   12402
tsd                  12327
dtype: int64

These columns appear to be categorical (less than 20 unique values):
Index([], dtype='object')

Unique value count for categorical columns:

Count of null values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
dtype: int64

Count of missing() values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
dtype: int64

Count of duplicated values:
0


In [13]:
# Let's convert settlement_date to datetime format
for key, value in uk_demand_clean.items():
    # Rename the columns
    uk_demand_clean[key] = dc.convert_to_datetime(value, columns=["settlement_date"])

In [14]:
# Checking again the daa types
ck.check(uk_demand_clean['2019'])

Number of columns: 4 and rows: 17520

Data types:
settlement_date      datetime64[ns]
settlement_period             int64
nd                            int64
tsd                           int64
dtype: object

Unique values count:
settlement_date        365
settlement_period       50
nd                   12402
tsd                  12327
dtype: int64

These columns appear to be categorical (less than 20 unique values):
Index([], dtype='object')

Unique value count for categorical columns:

Count of null values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
dtype: int64

Count of missing() values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
dtype: int64

Count of duplicated values:
0


In [15]:
# Let's found the dates with the daylight saving time change in all the yeas from the dataset
daylight_saving_time = ck.check_settlement_period(uk_demand_clean)

for year, periods in daylight_saving_time.items():
    print(f"Year: {year}, DST change dates:")
    for period_type, dates in periods.items():
        print(f"  {period_type}: {dates}")

Year: 2025, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2023, DST change dates:
  46_periods: DatetimeIndex(['2023-03-26'], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex(['2023-10-29'], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2019, DST change dates:
  46_periods: DatetimeIndex(['2019-03-31'], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex(['2019-10-27'], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2021, DST change dates:
  46_periods: DatetimeIndex(['2021-03-28'], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex(['2021-10-31'], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2022, DST change dates:
  46_periods: DatetimeIndex(['2022-03-27'], dtype=

The values correspond with the Daylight Saving Time in the UK for the data period:

- **2019**: Sun, Mar 31 – Sun, Oct 27  
- **2020**: Sun, Mar 29 – Sun, Oct 25  
- **2021**: Sun, Mar 28 – Sun, Oct 31  
- **2022**: Sun, Mar 27 – Sun, Oct 30  
- **2023**: Sun, Mar 26 – Sun, Oct 29  
- **2024**: Sun, Mar 31 – Sun, Oct 27  
- **2025**: Data ends on Mar 23, before Daylight Saving Time begins.

In [16]:
# Adjust the periods for daylight saving time
for key, value in uk_demand_clean.items():
    uk_demand_clean[key] = dc.adjust_dst_periods(value)

Adjusting periods for date: 2023-03-26 00:00:00
New legth for date 2023-03-26 00:00:00 is 48
Adjusting periods for date: 2023-10-29 00:00:00
New legth for date 2023-10-29 00:00:00 is 48
Adjusting periods for date: 2019-03-31 00:00:00
New legth for date 2019-03-31 00:00:00 is 48
Adjusting periods for date: 2019-10-27 00:00:00
New legth for date 2019-10-27 00:00:00 is 48
Adjusting periods for date: 2021-03-28 00:00:00
New legth for date 2021-03-28 00:00:00 is 48
Adjusting periods for date: 2021-10-31 00:00:00
New legth for date 2021-10-31 00:00:00 is 48
Adjusting periods for date: 2022-03-27 00:00:00
New legth for date 2022-03-27 00:00:00 is 48
Adjusting periods for date: 2022-10-30 00:00:00
New legth for date 2022-10-30 00:00:00 is 48
Adjusting periods for date: 2024-03-31 00:00:00
New legth for date 2024-03-31 00:00:00 is 48
Adjusting periods for date: 2024-10-27 00:00:00
New legth for date 2024-10-27 00:00:00 is 48
Adjusting periods for date: 2020-03-29 00:00:00
New legth for date 202

In [17]:
# Lets check the all the DST were adjusted
daylight_saving_time = ck.check_settlement_period(uk_demand_clean)

for year, periods in daylight_saving_time.items():
    print(f"Year: {year}, DST change dates:")
    for period_type, dates in periods.items():
        print(f"  {period_type}: {dates}")

Year: 2025, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2023, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2019, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2021, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
Year: 2022, DST change dates:
  46_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([],

In [18]:
# Adding bank holidays to the dataset
# The following dates are the bank holidays in the UK for the years 2019-2025 (end-date: 23-03-2025).
bank_holidays = ['01-01-2019', '19-04-2019', '22-04-2019', '06-05-2019', '27-05-2019',
                '26-08-2019', '25-12-2019', '26-12-2019', '01-01-2020', '10-04-2020',
                '13-04-2020', '08-05-2020', '25-05-2020', '31-08-2020', '25-12-2020',
                '28-12-2020', '01-01-2021', '02-04-2021', '05-04-2021', '03-05-2021',
                '31-05-2021', '30-08-2021', '27-12-2021', '28-12-2021','03-01-2022',
                '15-04-2022', '18-04-2022', '02-05-2022', '03-06-2022', '29-08-2022',
                '26-12-2022', '27-12-2022', '02-01-2023', '07-04-2023', '10-04-2023',
                '01-05-2023', '08-05-2023', '29-05-2023', '28-08-2023', '25-12-2023',
                '26-12-2023', '01-01-2024', '29-03-2024', '01-04-2024', '06-05-2024',
                '27-05-2024', '26-08-2024', '25-12-2024', '26-12-2024', '01-01-2025',
                '18-04-2025', '21-04-2025', '05-05-2025', '26-05-2025', '25-08-2025',
                '25-12-2025', '26-12-2025', '01-01-2026', '03-04-2026', '06-04-2026',
                '04-05-2026', '25-05-2026', '31-08-2026', '25-12-2026', '28-12-2026']

for key, value in uk_demand_clean.items():
    uk_demand_clean[key] = dc.add_holiday_column(value, bank_holidays)

**Holidays date from school might also be incorporated, but variate around the country, so for an specific region might be more useful**

In [19]:
uk_demand_clean['2019'].assign(
    settlement_date=uk_demand_clean['2019']['settlement_date'].dt.strftime('%Y-%m-%d')
)

settlement_date  settlement_period     nd    tsd  is_bank_holiday
0          2019-01-01                  1  23808  25291             True
1          2019-01-01                  2  24402  25720             True
2          2019-01-01                  3  24147  25495             True
3          2019-01-01                  4  23197  24590             True
4          2019-01-01                  5  22316  24346             True
...               ...                ...    ...    ...              ...
17517      2019-12-31                 46  27530  28817            False
17518      2019-12-31                 47  26765  27941            False
17519      2019-12-31                 48  26257  27230            False
17520      2019-03-31                  3  25165  26586            False
17521      2019-03-31                  4  24530  26151            False

[17520 rows x 5 columns]

In [20]:
# Let's check the data for 01 Apr 2024 that it is a bank holiday
uk_demand_clean['2024'][uk_demand_clean['2024']['settlement_date'] == '2024-04-01'].assign(
    settlement_date=uk_demand_clean['2019']['settlement_date'].dt.strftime('%Y-%m-%d')
)

settlement_date  settlement_period     nd    tsd  is_bank_holiday
4366      2019-04-02                  1  20610  22969             True
4367      2019-04-02                  2  20179  22661             True
4368      2019-04-02                  3  20079  22235             True
4369      2019-04-02                  4  20504  22695             True
4370      2019-04-02                  5  20323  22694             True
4371      2019-04-02                  6  20082  22498             True
4372      2019-04-02                  7  19849  22160             True
4373      2019-04-02                  8  19580  21892             True
4374      2019-04-02                  9  19328  21553             True
4375      2019-04-02                 10  19315  21456             True
4376      2019-04-02                 11  19312  21877             True
4377      2019-04-02                 12  19635  22183             True
4378      2019-04-02                 13  20809  23054             True
4379      2019-04-02                 14  21239  23245             True
4380      2019-04-02                 15  22043  23829             True
4381      2019-04-02                 16  22534  24085             True
4382      2019-04-02                 17  23034  24286             True
4383      2019-04-02                 18  23049  24151             True
4384      2019-04-02                 19  23309  24422             True
4385      2019-04-02                 20  23171  24406             True
4386      2019-04-02                 21  23171  24592             True
4387      2019-04-02                 22  23017  24444             True
4388      2019-04-02                 23  22806  23854             True
4389      2019-04-02                 24  23076  24217             True
4390      2019-04-02                 25  23959  24843             True
4391      2019-04-02                 26  24098  25122             True
4392      2019-04-02                 27  24164  25506             True
4393      2019-04-02                 28  24099  25550             True
4394      2019-04-02                 29  23751  25234             True
4395      2019-04-02                 30  23810  25293             True
4396      2019-04-02                 31  23780  25267             True
4397      2019-04-02                 32  24104  25591             True
4398      2019-04-02                 33  25061  26548             True
4399      2019-04-02                 34  26089  27576             True
4400      2019-04-02                 35  27657  29142             True
4401      2019-04-02                 36  28683  30169             True
4402      2019-04-02                 37  29387  30872             True
4403      2019-04-02                 38  29728  31211             True
4404      2019-04-02                 39  30007  31491             True
4405      2019-04-02                 40  30337  31821             True
4406      2019-04-02                 41  30687  32170             True
4407      2019-04-02                 42  30142  31628             True
4408      2019-04-02                 43  29290  30776             True
4409      2019-04-02                 44  28257  29746             True
4410      2019-04-02                 45  26959  28448             True
4411      2019-04-02                 46  25533  27023             True
4412      2019-04-02                 47  23706  25148             True
4413      2019-04-02                 48  22584  24035             True

In [21]:
# Merging the dataframes from the different years into one
uk_demand_merged = pd.concat(uk_demand_clean.values(), ignore_index=True)

uk_demand_merged.assign(
    settlement_date=uk_demand_merged['settlement_date'].dt.strftime('%Y-%m-%d')
)

settlement_date  settlement_period     nd    tsd  is_bank_holiday
0           2025-01-01                  1  21036  26215             True
1           2025-01-01                  2  21222  26063             True
2           2025-01-01                  3  21385  25734             True
3           2025-01-01                  4  20473  24988             True
4           2025-01-01                  5  19634  24912             True
...                ...                ...    ...    ...              ...
109147      2020-12-31                 46  30313  30925            False
109148      2020-12-31                 47  29399  30011            False
109149      2020-12-31                 48  28551  29165            False
109150      2020-03-29                  3  24271  25655            False
109151      2020-03-29                  4  23649  25155            False

[109152 rows x 5 columns]

In [22]:
# Ordering the dataframe by date and settlement period
uk_demand_merged = uk_demand_merged.sort_values(by=["settlement_date", "settlement_period"])
uk_demand_merged = uk_demand_merged.reset_index(drop=True)

In [23]:
# Check the data types, missing values, and duplicates
ck.check(uk_demand_merged)

Number of columns: 5 and rows: 109152

Data types:
settlement_date      datetime64[ns]
settlement_period             int64
nd                            int64
tsd                           int64
is_bank_holiday                bool
dtype: object

Unique values count:
settlement_date       2274
settlement_period       48
nd                   25987
tsd                  25152
is_bank_holiday          2
dtype: int64

These columns appear to be categorical (less than 20 unique values):
Index(['is_bank_holiday'], dtype='object')

Unique value count for categorical columns:

is_bank_holiday
False    106752
True       2400
Name: count, dtype: int64

Count of null values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
is_bank_holiday      0
dtype: int64

Count of missing() values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
is_bank_holiday      0
dtype: int64

Count of duplicated values:
0


##### Demand Data Update

In [24]:
# Adding to the data the last updates
file = os.path.join(uk_demand_path, 'demanddataupdate.csv')

# Read the file
df = pd.read_csv(file)
print(f'Update demand data loaded')

Update demand data loaded


In [25]:
# Snake case columns
uk_demand_update = dc.snake(df)

In [26]:
uk_demand_update.head()

settlement_date  settlement_period     nd forecast_actual_indicator    tsd  \
0      2025-03-01                  1  26764                         A  28817   
1      2025-03-01                  2  27403                         A  29289   
2      2025-03-01                  3  26928                         A  28662   
3      2025-03-01                  4  26300                         A  28172   
4      2025-03-01                  5  25852                         A  28331   

   england_wales_demand  embedded_wind_generation  embedded_wind_capacity  \
0                 24750                      1444                    6606   
1                 25324                      1444                    6606   
2                 24944                      1445                    6606   
3                 24431                      1445                    6606   
4                 24083                      1423                    6606   

   embedded_solar_generation  embedded_solar_capacity  non_bm_stor  \
0                          0                    18720            0   
1                          0                    18720            0   
2                          0                    18720            0   
3                          0                    18720            0   
4                          0                    18720            0   

   pump_storage_pumping  scottish_transfer  ifa_flow  ifa2_flow  britned_flow  \
0                    22               4053      1937        985          -263   
1                    17               4338      1943        992          -236   
2                    17               4401      1938        983            -3   
3                    62               4417      1938        983             0   
4                   675               4303      1998        991          -110   

   moyle_flow  east_west_flow  nemo_flow  nsl_flow  eleclink_flow  \
0           0               0        -62      1397            996   
1           0               0        -50      1397            996   
2         -35               0       -115      1397            998   
3          -6               0       -117      1397            997   
4        -118               0       -247      1397            997   

   viking_flow  greenlink_flow  
0         -816            -258  
1         -835            -139  
2         -719            -245  
3         -697            -390  
4         -222            -507

In [27]:
uk_demand_update.tail()

settlement_date  settlement_period  nd forecast_actual_indicator  tsd  \
2585      2025-04-23                 44   0                         F  500   
2586      2025-04-23                 45   0                         F  500   
2587      2025-04-23                 46   0                         F  500   
2588      2025-04-23                 47   0                         F  500   
2589      2025-04-23                 48   0                         F  500   

      england_wales_demand  embedded_wind_generation  embedded_wind_capacity  \
2585                     0                      1705                    6606   
2586                     0                      1705                    6606   
2587                     0                      1701                    6606   
2588                     0                      1701                    6606   
2589                     0                      1703                    6606   

      embedded_solar_generation  embedded_solar_capacity  non_bm_stor  \
2585                          0                    18766            0   
2586                          0                    18766            0   
2587                          0                    18766            0   
2588                          0                    18766            0   
2589                          0                    18766            0   

      pump_storage_pumping  scottish_transfer  ifa_flow  ifa2_flow  \
2585                     0                  0         0          0   
2586                     0                  0         0          0   
2587                     0                  0         0          0   
2588                     0                  0         0          0   
2589                     0                  0         0          0   

      britned_flow  moyle_flow  east_west_flow  nemo_flow  nsl_flow  \
2585             0           0               0          0         0   
2586             0           0               0          0         0   
2587             0           0               0          0         0   
2588             0           0               0          0         0   
2589             0           0               0          0         0   

      eleclink_flow  viking_flow  greenlink_flow  
2585              0            0               0  
2586              0            0               0  
2587              0            0               0  
2588              0            0               0  
2589              0            0               0

In [28]:
# Extracting necessary columns
uk_demand_update_cleaned = uk_demand_update[["settlement_date", "settlement_period", "nd", "tsd", "forecast_actual_indicator"]]

# Convert to datetime format
uk_demand_update_cleaned = dc.convert_to_datetime(uk_demand_update_cleaned, columns=["settlement_date"])

# Filter the data to include only the last updates
# If the forecast_actual_indicator is "A", it means it's an actual value
# If the forecast_actual_indicator is "F", it means it's a forecast value so wont be used
# The tsd column is the total system demand in MW and 500 MW is a placeholder value, so only values above 500 MW are considered
# The settlement_date should be greater than the maximum date in the merged dataset
uk_demand_update_cleaned = uk_demand_update_cleaned[(uk_demand_update_cleaned["forecast_actual_indicator"] == "A") & (uk_demand_update_cleaned["tsd"] > 500)]
uk_demand_update_cleaned = uk_demand_update_cleaned[uk_demand_update_cleaned["settlement_date"] > uk_demand_merged["settlement_date"].max()]
uk_demand_update_cleaned = uk_demand_update_cleaned.drop(columns=["forecast_actual_indicator"])

In [29]:
uk_demand_update_cleaned.head()

settlement_date  settlement_period     nd    tsd
1104      2025-03-24                  1  23427  25925
1105      2025-03-24                  2  24135  26637
1106      2025-03-24                  3  23810  26474
1107      2025-03-24                  4  23400  26030
1108      2025-03-24                  5  22679  25352

In [30]:
uk_demand_update_cleaned.tail()

settlement_date  settlement_period     nd    tsd
2208      2025-04-16                  3  21133  22352
2209      2025-04-16                  4  21151  22370
2210      2025-04-16                  5  20492  22462
2211      2025-04-16                  6  20165  22251
2212      2025-04-16                  7  19664  23178

In [31]:
# Lets check for DST
uk_demand_update_cleaned_dict = {"update": uk_demand_update_cleaned}
daylight_saving_time = ck.check_settlement_period(uk_demand_update_cleaned_dict)

for key, value in daylight_saving_time.items():
    for period_type, dates in value.items():
        print(f"  {period_type}: {dates}")

  46_periods: DatetimeIndex(['2025-03-30'], dtype='datetime64[ns]', name='settlement_date', freq=None)
  50_periods: DatetimeIndex([], dtype='datetime64[ns]', name='settlement_date', freq=None)


In [32]:
# Adjust the periods for daylight saving time
for key, value in uk_demand_update_cleaned_dict.items():
    uk_demand_update_cleaned = dc.adjust_dst_periods(value)

Adjusting periods for date: 2025-03-30 00:00:00
New legth for date 2025-03-30 00:00:00 is 48


In [33]:
# Add holiday column
uk_demand_update_cleaned = dc.add_holiday_column(uk_demand_update_cleaned, bank_holidays)

In [34]:
uk_demand_update_cleaned.head()

settlement_date  settlement_period     nd    tsd  is_bank_holiday
0      2025-03-24                  1  23427  25925            False
1      2025-03-24                  2  24135  26637            False
2      2025-03-24                  3  23810  26474            False
3      2025-03-24                  4  23400  26030            False
4      2025-03-24                  5  22679  25352            False

In [62]:
# Concating with the historical data and ordering the dataframe by date and settlement period
uk_demand_merged_update = pd.concat([uk_demand_merged, uk_demand_update_cleaned], ignore_index=True)
uk_demand_merged_update = uk_demand_merged_update.sort_values(by=["settlement_date", "settlement_period"])
uk_demand_merged_update = uk_demand_merged_update.reset_index(drop=True)
ck.check(uk_demand_merged_update)

Number of columns: 5 and rows: 110263

Data types:
settlement_date      datetime64[ns]
settlement_period             int64
nd                            int64
tsd                           int64
is_bank_holiday                bool
dtype: object

Unique values count:
settlement_date       2298
settlement_period       48
nd                   26012
tsd                  25176
is_bank_holiday          2
dtype: int64

These columns appear to be categorical (less than 20 unique values):
Index(['is_bank_holiday'], dtype='object')

Unique value count for categorical columns:

is_bank_holiday
False    107863
True       2400
Name: count, dtype: int64

Count of null values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
is_bank_holiday      0
dtype: int64

Count of missing() values:
settlement_date      0
settlement_period    0
nd                   0
tsd                  0
is_bank_holiday      0
dtype: int64

Count of duplicated values:
0


In [63]:
uk_demand_merged_update.head()

settlement_date  settlement_period     nd    tsd  is_bank_holiday
0      2019-01-01                  1  23808  25291             True
1      2019-01-01                  2  24402  25720             True
2      2019-01-01                  3  24147  25495             True
3      2019-01-01                  4  23197  24590             True
4      2019-01-01                  5  22316  24346             True

In [64]:
uk_demand_merged_update.tail()

settlement_date  settlement_period     nd    tsd  is_bank_holiday
110258      2025-04-16                  3  21133  22352            False
110259      2025-04-16                  4  21151  22370            False
110260      2025-04-16                  5  20492  22462            False
110261      2025-04-16                  6  20165  22251            False
110262      2025-04-16                  7  19664  23178            False

In [65]:
# Saving the data to a CSV file
uk_demand_merged_update = dc.drop_nan_rows(uk_demand_merged_update)
uk_demand_merged_update = uk_demand_merged_update.sort_values(by=["settlement_date", "settlement_period"])
uk_demand_merged_update.to_csv(os.path.join(uk_demand_path, "uk_demand_merged.csv"), index=False)
print("Data saved to uk_demand_merged.csv")

Number of rows dropped due to NaN values: 0
Data saved to uk_demand_merged.csv


In [39]:
# Adding rolling and lag features in a dictionary since they will be used for different models
uk_demand_merge_updated_for_ml_dict = {}
keys = ["30_min", "1_hour", "2 hour", "3_hours", "6_hours", "12_hours", "1_day", "2_day", "3_days", "5_days", "1_week", "2_week"]
for key in keys:

    # Create a copy of the dataframe with the last updates for each key
    uk_demand_merged_update_shifted = uk_demand_merged_update.copy()

    if key == "30_min":
        pos = 0
    if key == "1_hour":
        pos = 1
    if key == "2 hour":
        pos = 2
    if key == "3_hours":
        pos = 3
    if key == "6_hours":
        pos = 4
    if key == "12_hours":
        pos = 5
    if key == "1_day":
        pos = 6
    if key == "2_day":
        pos = 7
    if key == "3_days":
        pos = 8
    if key == "5_days":
        pos = 9
    if key == "1_week":
        pos = 10
    if key == "2_week":
        pos = 11

    # Adding rolling features
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=6, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=8, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='hours', window_size=12, pos=pos)

    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='days', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='days', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='days', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='days', window_size=5, pos=pos)

    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='weeks', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='weeks', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='weeks', window_size=3, pos=pos)

    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='months', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='months', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='months', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='months', window_size=6, pos=pos)
    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='months', window_size=9, pos=pos)

    uk_demand_merged_update_shifted = dc.create_rolling_features(uk_demand_merged_update_shifted, columns=["nd", "tsd"], type='years', window_size=1, pos=pos)

    # Adding lag features
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=6, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=12, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='hours', window_size=8, pos=pos)

    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='days', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='days', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='days', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='days', window_size=5, pos=pos)

    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='weeks', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='weeks', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='weeks', window_size=3, pos=pos)

    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='months', window_size=1, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='months', window_size=2, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='months', window_size=3, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='months', window_size=6, pos=pos)
    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='months', window_size=9, pos=pos)

    uk_demand_merged_update_shifted = dc.create_lag_features(uk_demand_merged_update_shifted, columns=['nd', 'tsd'], type='years', window_size=1, pos=pos)

    # Drop the rows with NaN values
    length = len(uk_demand_merged_update_shifted)
    uk_demand_merged_update_shifted = uk_demand_merged_update_shifted.dropna()
    # Check if the length of the dataframe has changed
    if length != len(uk_demand_merged_update_shifted):
        print(f"For key {key}, length changed from {length} to {len(uk_demand_merged_update_shifted)}")

    # Drop the columns that are not needed. Only keeping the target and lag and rolling features
    uk_demand_merged_update_shifted = uk_demand_merged_update_shifted.drop(columns=["tsd"])

    # Merging the new featuresd with the original dataframe
    uk_demand_merge_updated_for_ml_dict[key] = uk_demand_merged_update_shifted


For key 30_min, length changed from 110263 to 92742
For key 1_hour, length changed from 110263 to 92741
For key 2 hour, length changed from 110263 to 92739
For key 3_hours, length changed from 110263 to 92737
For key 6_hours, length changed from 110263 to 92731
For key 12_hours, length changed from 110263 to 92719
For key 1_day, length changed from 110263 to 92695
For key 2_day, length changed from 110263 to 92647
For key 3_days, length changed from 110263 to 92599
For key 5_days, length changed from 110263 to 92503
For key 1_week, length changed from 110263 to 92407
For key 2_week, length changed from 110263 to 92071


In [41]:
 uk_demand_merge_updated_for_ml_dict["30_min"].head()

settlement_date  settlement_period     nd  is_bank_holiday  \
17521      2020-01-01                  2  26921             True   
17522      2020-01-01                  3  26569             True   
17523      2020-01-01                  4  25754             True   
17524      2020-01-01                  5  25075             True   
17525      2020-01-01                  6  24468             True   

       nd_rolling_1_hours_for_30_min  nd_rolling_std_1_hours_for_30_min  \
17521                        26298.5                          58.689863   
17522                        26630.5                         410.829040   
17523                        26745.0                         248.901587   
17524                        26161.5                         576.292027   
17525                        25414.5                         480.125504   

       nd_rolling_max_1_hours_for_30_min  nd_rolling_min_1_hours_for_30_min  \
17521                            26340.0                            26257.0   
17522                            26921.0                            26340.0   
17523                            26921.0                            26569.0   
17524                            26569.0                            25754.0   
17525                            25754.0                            25075.0   

       tsd_rolling_1_hours_for_30_min  tsd_rolling_std_1_hours_for_30_min  \
17521                         27191.5                           54.447222   
17522                         27418.5                          375.473701   
17523                         27462.0                          313.955411   
17524                         26837.5                          569.220959   
17525                         26129.5                          432.042243   

       tsd_rolling_max_1_hours_for_30_min  tsd_rolling_min_1_hours_for_30_min  \
17521                             27230.0                             27153.0   
17522                             27684.0                             27153.0   
17523                             27684.0                             27240.0   
17524                             27240.0                             26435.0   
17525                             26435.0                             25824.0   

       nd_rolling_2_hours_for_30_min  nd_rolling_std_2_hours_for_30_min  \
17521                       26723.00                         582.196416   
17522                       26570.75                         322.538241   
17523                       26521.75                         297.073925   
17524                       26396.00                         490.188399   
17525                       26079.75                         829.196951   

       nd_rolling_max_2_hours_for_30_min  nd_rolling_min_2_hours_for_30_min  \
17521                            27530.0                            26257.0   
17522                            26921.0                            26257.0   
17523                            26921.0                            26257.0   
17524                            26921.0                            25754.0   
17525                            26921.0                            25075.0   

       tsd_rolling_2_hours_for_30_min  tsd_rolling_std_2_hours_for_30_min  \
17521                        27785.25                          773.909717   
17522                        27502.00                          374.891095   
17523                        27326.75                          241.317737   
17524                        27128.00                          517.221423   
17525                        26795.75                          828.811348   

       tsd_rolling_max_2_hours_for_30_min  tsd_rolling_min_2_hours_for_30_min  \
17521                             28817.0                             27153.0   
17522                             27941.0                             27153.0   
17523                             27684.0                             27153.0   
17524   

In [42]:
 uk_demand_merge_updated_for_ml_dict["30_min"].tail()

settlement_date  settlement_period     nd  is_bank_holiday  \
110258      2025-04-16                  3  21133            False   
110259      2025-04-16                  4  21151            False   
110260      2025-04-16                  5  20492            False   
110261      2025-04-16                  6  20165            False   
110262      2025-04-16                  7  19664            False   

        nd_rolling_1_hours_for_30_min  nd_rolling_std_1_hours_for_30_min  \
110258                        21525.0                          87.681241   
110259                        21298.0                         233.345238   
110260                        21142.0                          12.727922   
110261                        20821.5                         465.983369   
110262                        20328.5                         231.223917   

        nd_rolling_max_1_hours_for_30_min  nd_rolling_min_1_hours_for_30_min  \
110258                            21587.0                            21463.0   
110259                            21463.0                            21133.0   
110260                            21151.0                            21133.0   
110261                            21151.0                            20492.0   
110262                            20492.0                            20165.0   

        tsd_rolling_1_hours_for_30_min  tsd_rolling_std_1_hours_for_30_min  \
110258                         22718.0                           50.911688   
110259                         22517.0                          233.345238   
110260                         22361.0                           12.727922   
110261                         22416.0                           65.053824   
110262                         22356.5                          149.199531   

        tsd_rolling_max_1_hours_for_30_min  \
110258                             22754.0   
110259                             22682.0   
110260                             22370.0   
110261                             22462.0   
110262                             22462.0   

        tsd_rolling_min_1_hours_for_30_min  nd_rolling_2_hours_for_30_min  \
110258                             22682.0                       22222.25   
110259                             22352.0                       21634.50   
110260                             22352.0                       21333.50   
110261                             22370.0                       21059.75   
110262                             22251.0                       20735.25   

        nd_rolling_std_2_hours_for_30_min  nd_rolling_max_2_hours_for_30_min  \
110258                         929.092523                            23484.0   
110259                         517.136668                            22355.0   
110260                         226.964755                            21587.0   
110261                         407.693819                            21463.0   
110262                         488.333476                            21151.0   

        nd_rolling_min_2_hours_for_30_min  tsd_rolling_2_hours_for_30_min  \
110258                            21463.0                        23358.50   
110259                            21133.0                        22797.25   
110260                            21133.0                        22539.50   
110261                            20492.0                        22466.50   
110262                            20165.0                        22358.75   

        tsd_rolling_std_2_hours_for_30_min  \
110258                          886.709460   
110259                          438.905742   
110260                          208.329067   
110261                          151.528875   
110262                           86.492293   

        tsd_rolling_max_2_hours_for_30_min  \
110258                             24597.0   
110259                             23401.0   
110260                             22754.0   
110261                             22682

### Carbon Intensity and Generation Mix

In [66]:
carbon_path = os.path.join(file_path, "carbon_intensity")

#### UK

In [67]:
# Exploring the data
uk_carbon_path = os.path.join(carbon_path, "uk")

# Read the files in the directory
file_list = glob.glob(os.path.join(uk_carbon_path, 'df_fuel*.csv'))

# Initialize an empty dictionary to store the dataframes
carbon = {}

# Loop through the files and read them into a dictionary
for file in file_list:

    # Read the file
    df = pd.read_csv(file)
    carbon['uk'] = df

    print(f'carbon intensity loaded')

carbon intensity loaded


In [68]:
carbon['uk'].head()

DATETIME     GAS     COAL  NUCLEAR   WIND  WIND_EMB  HYDRO  \
0  2009-01-01T00:00:00  8369.0  15037.0   7099.0  237.0      59.0    246   
1  2009-01-01T00:30:00  8501.0  15095.0   7087.0  218.0      54.0    245   
2  2009-01-01T01:00:00  8475.0  15087.0   7074.0  196.0      49.0    246   
3  2009-01-01T01:30:00  8320.0  15031.0   7064.0  181.0      45.0    246   
4  2009-01-01T02:00:00  8295.0  14999.0   7052.0  167.0      42.0    246   

   IMPORTS  BIOMASS  OTHER  SOLAR  STORAGE  GENERATION  CARBON_INTENSITY  \
0   2524.0      0.0    0.0    0.0        0     33571.0             525.0   
1   2502.0      0.0    0.0    0.0        0     33703.0             526.0   
2   2472.0      0.0    0.0    0.0        0     33599.0             527.0   
3   2445.0      0.0    0.0    0.0        0     33332.0             527.0   
4   2370.0      0.0    0.0    0.0        0     33170.0             528.0   

   LOW_CARBON  ZERO_CARBON  RENEWABLE   FOSSIL  GAS_perc  COAL_perc  \
0      7641.0       7581.0      542.0  23406.0      24.9       44.8   
1      7605.0       7550.0      517.0  23596.0      25.2       44.8   
2      7565.0       7516.0      491.0  23562.0      25.2       44.9   
3      7536.0       7491.0      472.0  23351.0      25.0       45.1   
4      7506.0       7464.0      454.0  23294.0      25.0       45.2   

   NUCLEAR_perc  WIND_perc  WIND_EMB_perc  HYDRO_perc  IMPORTS_perc  \
0          21.1        0.7            0.2         0.7           7.5   
1          21.0        0.6            0.2         0.7           7.4   
2          21.1        0.6            0.1         0.7           7.4   
3          21.2        0.5            0.1         0.7           7.3   
4          21.3        0.5            0.1         0.7           7.1   

   BIOMASS_perc  OTHER_perc  SOLAR_perc  STORAGE_perc  GENERATION_perc  \
0           0.0         0.0         0.0           0.0            100.0   
1           0.0         0.0         0.0           0.0            100.0   
2           0.0         0.0         0.0           0.0            100.0   
3           0.0         0.0         0.0           0.0            100.0   
4           0.0         0.0         0.0           0.0            100.0   

   LOW_CARBON_perc  ZERO_CARBON_perc  RENEWABLE_perc  FOSSIL_perc  
0             22.8              24.5             1.6         69.7  
1             22.6              24.2             1.5         70.0  
2             22.5              24.2             1.5         70.1  
3             22.6              24.3             1.4         70.1  
4             22.6              24.3             1.4         70.2

##### Dataset Column Descriptions

| **Column Name**       | **Description**                                                                                                                                                                                                 |
|------------------------|-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| **DATETIME**           | The date and time when the data was recorded.                                                       |
| **GAS**                | The amount of electricity generated from gas-powered sources, measured in megawatt-hours (MWh).                                                                                                       |
| **COAL**               | The amount of electricity generated from coal-powered sources, measured in megawatt-hours (MWh).                                                                                                   |
| **NUCLEAR**            | The amount of electricity generated from nuclear energy, measured in megawatt-hours (MWh).                                                                                                         |
| **WIND**               | The amount of electricity generated from wind power, measured in megawatt-hours (MWh).                                                                                                             |
| **WIND_EMB**           | Estimated electricity generated by small, non-grid-connected wind farms. These farms reduce grid demand but are hard to measure directly — this is a modeled estimate.                                        |
| **HYDRO**              | The amount of electricity generated from hydroelectric power, measured in megawatt-hours (MWh).                                                                                                   |
| **IMPORTS**            | The amount of electricity imported from other regions or countries, measured in megawatt-hours (MWh).                                                                                             |
| **BIOMASS**            | The amount of electricity generated from biomass, measured in megawatt-hours (MWh).                                                                                                                |
| **OTHER**              | The amount of electricity generated from other non-renewable or non-typical sources, measured in megawatt-hours (MWh).                                                                             |
| **SOLAR**              | The amount of electricity generated from solar power, measured in megawatt-hours (MWh).                                                                                                            |
| **STORAGE**            | The amount of electricity stored in batteries or other storage technologies, measured in megawatt-hours (MWh).                                                                                     |
| **GENERATION**         | The total electricity generation across all sources in the dataset, measured in megawatt-hours (MWh).                                                                                              |
| **CARBON_INTENSITY**   | The amount of carbon emissions associated with the electricity generated, measured in grams of CO2 per kilowatt-hour (gCO2/kWh). This helps assess the environmental impact of electricity generation. |
| **LOW_CARBON**         | The amount of electricity generated from low-carbon sources (such as solar, wind, hydro, biomass and nuclear), measured in megawatt-hours (MWh).                                                           |
| **ZERO_CARBON**        | The amount of electricity generated from zero-carbon sources (such as wind, solar, and hydro), measured in megawatt-hours (MWh).                                                                    |
| **RENEWABLE**          | The amount of electricity generated from renewable sources (such as wind, solar, hydro, and biomass), measured in megawatt-hours (MWh).                                                             |
| **FOSSIL**             | The amount of electricity generated from fossil fuels (such as gas, coal, and oil), measured in megawatt-hours (MWh).                                                                               |
| **GAS_perc**           | The percentage of total electricity generation that comes from gas-powered sources. This is calculated as `(GAS / GENERATION) * 100`.                                                                         |
| **COAL_perc**          | The percentage of total electricity generation that comes from coal-powered sources. This is calculated as `(COAL / GENERATION) * 100`.                                                                       |
| **NUCLEAR_perc**       | The percentage of total electricity generation that comes from nuclear power. This is calculated as `(NUCLEAR / GENERATION) * 100`.                                                                           |
| **WIND_perc**          | The percentage of total electricity generation that comes from wind power. This is calculated as `(WIND / GENERATION) * 100`.                                                                                 |
| **WIND_EMB_perc**      | The percentage of total electricity generation that comes from wind power, non-grid-connected wind farms. This is calculated as `(WIND_EMB / GENERATION) * 100`.                                              |
| **HYDRO_perc**         | The percentage of total electricity generation that comes from hydroelectric power. This is calculated as `(HYDRO / GENERATION) * 100`.                                                                       |
| **IMPORTS_perc**       | The percentage of total electricity generation that comes from imported electricity. This is calculated as `(IMPORTS / GENERATION) * 100`.                                                                     |
| **BIOMASS_perc**       | The percentage of total electricity generation that comes from biomass. This is calculated as `(BIOMASS / GENERATION) * 100`.                                                                                 |
| **OTHER_perc**         | The percentage of total electricity generation that comes from other non-renewable or non-typical sources. This is calculated as `(OTHER / GENERATION) * 100`.                                                |
| **SOLAR_perc**         | The percentage of total electricity generation that comes from solar power. This is calculated as `(SOLAR / GENERATION) * 100`.                                                                               |
| **STORAGE_perc**       | The percentage of total electricity generation that comes from electricity storage. This is calculated as `(STORAGE / GENERATION) * 100`.                                                                     |
| **GENERATION_perc**    | The total percentage of electricity generation. Typically, this would be `100%` unless you have some form of normalization or scaling.                                                                        |
| **LOW_CARBON_perc**    | The percentage of total electricity generation that comes from low-carbon sources. This is calculated as `(LOW_CARBON / GENERATION) * 100`.                                                                   |
| **ZERO_CARBON_perc**   | The percentage of total electricity generation that comes from zero-carbon sources. This is calculated as `(ZERO_CARBON / GENERATION) * 100`.                                                                  |
| **RENEWABLE_perc**     | The percentage of total electricity generation that comes from renewable sources. This is calculated as `(RENEWABLE / GENERATION) * 100`.                                                                     |
| **FOSSIL_perc**        | The percentage of total electricity generation that comes from fossil fuel sources. This is calculated as `(FOSSIL / GENERATION) * 100`.                                                                       |


In [69]:
# Snake case columns
for key, value in carbon.items():
    # Rename the columns
    carbon[key] = dc.snake(value)

In [70]:
# Let's convert datetime to datetime format
for key, value in carbon.items():
    # Rename the columns
    carbon[key] = dc.convert_to_datetime(value, columns=["datetime"])

In [71]:
ck.check(carbon['uk'])

Number of columns: 34 and rows: 285570

Data types:
datetime            datetime64[ns]
gas                        float64
coal                       float64
nuclear                    float64
wind                       float64
wind_emb                   float64
hydro                        int64
imports                    float64
biomass                    float64
other                      float64
solar                      float64
storage                      int64
generation                 float64
carbon_intensity           float64
low_carbon                 float64
zero_carbon                float64
renewable                  float64
fossil                     float64
gas_perc                   float64
coal_perc                  float64
nuclear_perc               float64
wind_perc                  float64
wind_emb_perc              float64
hydro_perc                 float64
imports_perc               float64
biomass_perc               float64
other_perc                 float64
sol

In [72]:
carbon['uk'].head()

datetime     gas     coal  nuclear   wind  wind_emb  hydro  \
0 2009-01-01 00:00:00  8369.0  15037.0   7099.0  237.0      59.0    246   
1 2009-01-01 00:30:00  8501.0  15095.0   7087.0  218.0      54.0    245   
2 2009-01-01 01:00:00  8475.0  15087.0   7074.0  196.0      49.0    246   
3 2009-01-01 01:30:00  8320.0  15031.0   7064.0  181.0      45.0    246   
4 2009-01-01 02:00:00  8295.0  14999.0   7052.0  167.0      42.0    246   

   imports  biomass  other  solar  storage  generation  carbon_intensity  \
0   2524.0      0.0    0.0    0.0        0     33571.0             525.0   
1   2502.0      0.0    0.0    0.0        0     33703.0             526.0   
2   2472.0      0.0    0.0    0.0        0     33599.0             527.0   
3   2445.0      0.0    0.0    0.0        0     33332.0             527.0   
4   2370.0      0.0    0.0    0.0        0     33170.0             528.0   

   low_carbon  zero_carbon  renewable   fossil  gas_perc  coal_perc  \
0      7641.0       7581.0      542.0  23406.0      24.9       44.8   
1      7605.0       7550.0      517.0  23596.0      25.2       44.8   
2      7565.0       7516.0      491.0  23562.0      25.2       44.9   
3      7536.0       7491.0      472.0  23351.0      25.0       45.1   
4      7506.0       7464.0      454.0  23294.0      25.0       45.2   

   nuclear_perc  wind_perc  wind_emb_perc  hydro_perc  imports_perc  \
0          21.1        0.7            0.2         0.7           7.5   
1          21.0        0.6            0.2         0.7           7.4   
2          21.1        0.6            0.1         0.7           7.4   
3          21.2        0.5            0.1         0.7           7.3   
4          21.3        0.5            0.1         0.7           7.1   

   biomass_perc  other_perc  solar_perc  storage_perc  generation_perc  \
0           0.0         0.0         0.0           0.0            100.0   
1           0.0         0.0         0.0           0.0            100.0   
2           0.0         0.0         0.0           0.0            100.0   
3           0.0         0.0         0.0           0.0            100.0   
4           0.0         0.0         0.0           0.0            100.0   

   low_carbon_perc  zero_carbon_perc  renewable_perc  fossil_perc  
0             22.8              24.5             1.6         69.7  
1             22.6              24.2             1.5         70.0  
2             22.5              24.2             1.5         70.1  
3             22.6              24.3             1.4         70.1  
4             22.6              24.3             1.4         70.2

In [73]:
carbon['uk'] = carbon['uk'][carbon['uk']["datetime"] >= '2019-01-01']

In [74]:
carbon['uk'].head()

datetime     gas  coal  nuclear    wind  wind_emb  hydro  \
175296 2019-01-01 00:00:00  5853.0   0.0   6924.0  9236.0    2031.0    405   
175297 2019-01-01 00:30:00  6292.0   0.0   6838.0  9297.0    1997.0    388   
175298 2019-01-01 01:00:00  5719.0   0.0   6834.0  9356.0    1959.0    372   
175299 2019-01-01 01:30:00  5020.0   0.0   6830.0  9135.0    1914.0    368   
175300 2019-01-01 02:00:00  4964.0   0.0   6827.0  8912.0    1865.0    355   

        imports  biomass  other  solar  storage  generation  carbon_intensity  \
175296   1734.0   1052.0   64.0    0.0        0     27299.0              94.0   
175297   1750.0   1040.0   63.0    0.0       24     27689.0              99.0   
175298   2092.0   1026.0   64.0    0.0        0     27422.0              97.0   
175299   2104.0   1022.0   63.0    0.0        0     26456.0              90.0   
175300   2203.0   1018.0   63.0    0.0        0     26207.0              91.0   

        low_carbon  zero_carbon  renewable  fossil  gas_perc  coal_perc  \
175296     19648.0      16565.0    11672.0  5853.0      21.4        0.0   
175297     19584.0      16547.0    11706.0  6292.0      22.7        0.0   
175298     19547.0      16562.0    11687.0  5719.0      20.9        0.0   
175299     19269.0      16333.0    11417.0  5020.0      19.0        0.0   
175300     18977.0      16094.0    11132.0  4964.0      18.9        0.0   

        nuclear_perc  wind_perc  wind_emb_perc  hydro_perc  imports_perc  \
175296          25.4       33.8            7.4         1.5           6.4   
175297          24.7       33.6            7.2         1.4           6.3   
175298          24.9       34.1            7.1         1.4           7.6   
175299          25.8       34.5            7.2         1.4           8.0   
175300          26.1       34.0            7.1         1.4           8.4   

        biomass_perc  other_perc  solar_perc  storage_perc  generation_perc  \
175296           3.9         0.2         0.0           0.0            100.0   
175297           3.8         0.2         0.0           0.1            100.0   
175298           3.7         0.2         0.0           0.0            100.0   
175299           3.9         0.2         0.0           0.0            100.0   
175300           3.9         0.2         0.0           0.0            100.0   

        low_carbon_perc  zero_carbon_perc  renewable_perc  fossil_perc  
175296             72.0              70.4            42.8         21.4  
175297             70.7              69.1            42.3         22.7  
175298             71.3              70.9            42.6         20.9  
175299             72.8              72.8            43.2         19.0  
175300             72.4              72.7            42.5         18.9

In [75]:
# Dropping generation_percent column becuase this would create data leakage
carbon['uk'] = carbon['uk'].drop(columns=["generation_perc"])

# Dropping other columns that are not needed.
carbon['uk'] = carbon['uk'].drop(columns=[col for col in carbon['uk'].columns if 'perc' in col])

In [76]:
carbon['uk'].head()

datetime     gas  coal  nuclear    wind  wind_emb  hydro  \
175296 2019-01-01 00:00:00  5853.0   0.0   6924.0  9236.0    2031.0    405   
175297 2019-01-01 00:30:00  6292.0   0.0   6838.0  9297.0    1997.0    388   
175298 2019-01-01 01:00:00  5719.0   0.0   6834.0  9356.0    1959.0    372   
175299 2019-01-01 01:30:00  5020.0   0.0   6830.0  9135.0    1914.0    368   
175300 2019-01-01 02:00:00  4964.0   0.0   6827.0  8912.0    1865.0    355   

        imports  biomass  other  solar  storage  generation  carbon_intensity  \
175296   1734.0   1052.0   64.0    0.0        0     27299.0              94.0   
175297   1750.0   1040.0   63.0    0.0       24     27689.0              99.0   
175298   2092.0   1026.0   64.0    0.0        0     27422.0              97.0   
175299   2104.0   1022.0   63.0    0.0        0     26456.0              90.0   
175300   2203.0   1018.0   63.0    0.0        0     26207.0              91.0   

        low_carbon  zero_carbon  renewable  fossil  
175296     19648.0      16565.0    11672.0  5853.0  
175297     19584.0      16547.0    11706.0  6292.0  
175298     19547.0      16562.0    11687.0  5719.0  
175299     19269.0      16333.0    11417.0  5020.0  
175300     18977.0      16094.0    11132.0  4964.0

In [77]:
# Extracting setellment period and settlement date from datetime
carbon['uk'] = dc.extract_settlement_period_and_date(carbon['uk'], "datetime")

In [78]:
carbon['uk'].head()

gas  coal  nuclear    wind  wind_emb  hydro  imports  biomass  \
175296  5853.0   0.0   6924.0  9236.0    2031.0    405   1734.0   1052.0   
175297  6292.0   0.0   6838.0  9297.0    1997.0    388   1750.0   1040.0   
175298  5719.0   0.0   6834.0  9356.0    1959.0    372   2092.0   1026.0   
175299  5020.0   0.0   6830.0  9135.0    1914.0    368   2104.0   1022.0   
175300  4964.0   0.0   6827.0  8912.0    1865.0    355   2203.0   1018.0   

        other  solar  storage  generation  carbon_intensity  low_carbon  \
175296   64.0    0.0        0     27299.0              94.0     19648.0   
175297   63.0    0.0       24     27689.0              99.0     19584.0   
175298   64.0    0.0        0     27422.0              97.0     19547.0   
175299   63.0    0.0        0     26456.0              90.0     19269.0   
175300   63.0    0.0        0     26207.0              91.0     18977.0   

        zero_carbon  renewable  fossil settlement_date  settlement_period  
175296      16565.0    11672.0  5853.0      2019-01-01                  1  
175297      16547.0    11706.0  6292.0      2019-01-01                  2  
175298      16562.0    11687.0  5719.0      2019-01-01                  3  
175299      16333.0    11417.0  5020.0      2019-01-01                  4  
175300      16094.0    11132.0  4964.0      2019-01-01                  5

In [79]:
# Adding new columns for the carbon intensity prediction
carbon['uk'] = dc.create_carbon_columns(carbon['uk'])

In [80]:
carbon['uk'].tail()

gas  coal  nuclear     wind  wind_emb  hydro  imports  biomass  \
285565  4952.0   0.0   4417.0  13805.0    3656.0    191   4080.0   1152.0   
285566  5400.0   0.0   4415.0  14010.0    3760.0    198   4796.0   1154.0   
285567  5546.0   0.0   4410.0  13745.0    3810.0    192   4872.0   1163.0   
285568  5540.0   0.0   4414.0  13574.0    3841.0    142   5134.0   1160.0   
285569  4926.0   0.0   4409.0  13699.0    3907.0    141   5152.0   1155.0   

         other   solar  storage  generation  carbon_intensity  low_carbon  \
285565  1100.0  1151.0        0     34504.0              71.0     24372.0   
285566   906.0  1800.0        0     36439.0              73.0     25337.0   
285567   894.0  2632.0        0     37264.0              73.0     25952.0   
285568   677.0  3448.0        0     37930.0              70.0     26579.0   
285569   670.0  4257.0        0     38316.0              63.0     27568.0   

        zero_carbon  renewable  fossil settlement_date  settlement_period  \
285565      18413.0    18803.0  4952.0      2025-04-16                 14   
285566      18623.0    19768.0  5400.0      2025-04-16                 15   
285567      18347.0    20379.0  5546.0      2025-04-16                 16   
285568      18130.0    21005.0  5540.0      2025-04-16                 17   
285569      18249.0    22004.0  4926.0      2025-04-16                 18   

        low_vs_fossil  zero_vs_fossil  renewable_vs_fossil  green_score  
285565       4.921648        3.718296             3.797052   210.647887  
285566       4.692037        3.448704             3.660741   216.575342  
285567       4.679409        3.308150             3.674540   224.342466  
285568       4.797653        3.272563             3.791516   243.171429  
285569       5.596427        3.704629             4.466910   285.015873

In [81]:
ck.check(carbon['uk'])

Number of columns: 23 and rows: 110274

Data types:
gas                           float64
coal                          float64
nuclear                       float64
wind                          float64
wind_emb                      float64
hydro                           int64
imports                       float64
biomass                       float64
other                         float64
solar                         float64
storage                         int64
generation                    float64
carbon_intensity              float64
low_carbon                    float64
zero_carbon                   float64
renewable                     float64
fossil                        float64
settlement_date        datetime64[ns]
settlement_period               int32
low_vs_fossil                 float64
zero_vs_fossil                float64
renewable_vs_fossil           float64
green_score                   float64
dtype: object

Unique values count:
gas                     22346
coal    

In [82]:
# Saving the data to a CSV file
carbon['uk'] = dc.drop_nan_rows(carbon['uk'])
carbon['uk'] = carbon['uk'].sort_values(by=["settlement_date", "settlement_period"])
carbon['uk'].to_csv(os.path.join(uk_carbon_path, "carbon_and_mix.csv"), index=False)
print("Data saved to carbon_and_mix.csv")

Number of rows dropped due to NaN values: 0
Data saved to carbon_and_mix.csv


In [83]:
# Merging with demand data
data_uk_merged = pd.merge(uk_demand_merged_update, carbon['uk'], how="left", left_on=["settlement_date", "settlement_period"], right_on=["settlement_date", "settlement_period"])
lenght = len(data_uk_merged)
data_uk_merged = dc.drop_nan_rows(data_uk_merged)
if lenght != len(data_uk_merged):
    print(f"Length changed from {lenght} to {len(data_uk_merged)}")

# Modify the date column to include the time
data_uk_merged = dc.add_time(data_uk_merged, "settlement_date")

data_uk_merged = data_uk_merged.sort_values(by=["settlement_date", "settlement_period"])
data_uk_merged = data_uk_merged.reset_index(drop=True)
data_uk_merged.head()

Number of rows dropped due to NaN values: 0


settlement_date  settlement_period     nd    tsd  is_bank_holiday  \
0 2019-01-01 00:00:00                  1  23808  25291             True   
1 2019-01-01 00:30:00                  2  24402  25720             True   
2 2019-01-01 01:00:00                  3  24147  25495             True   
3 2019-01-01 01:30:00                  4  23197  24590             True   
4 2019-01-01 02:00:00                  5  22316  24346             True   

      gas  coal  nuclear    wind  wind_emb  hydro  imports  biomass  other  \
0  5853.0   0.0   6924.0  9236.0    2031.0    405   1734.0   1052.0   64.0   
1  6292.0   0.0   6838.0  9297.0    1997.0    388   1750.0   1040.0   63.0   
2  5719.0   0.0   6834.0  9356.0    1959.0    372   2092.0   1026.0   64.0   
3  5020.0   0.0   6830.0  9135.0    1914.0    368   2104.0   1022.0   63.0   
4  4964.0   0.0   6827.0  8912.0    1865.0    355   2203.0   1018.0   63.0   

   solar  storage  generation  carbon_intensity  low_carbon  zero_carbon  \
0    0.0        0     27299.0              94.0     19648.0      16565.0   
1    0.0       24     27689.0              99.0     19584.0      16547.0   
2    0.0        0     27422.0              97.0     19547.0      16562.0   
3    0.0        0     26456.0              90.0     19269.0      16333.0   
4    0.0        0     26207.0              91.0     18977.0      16094.0   

   renewable  fossil  low_vs_fossil  zero_vs_fossil  renewable_vs_fossil  \
0    11672.0  5853.0       3.356911        2.830173             1.994191   
1    11706.0  6292.0       3.112524        2.629847             1.860458   
2    11687.0  5719.0       3.417905        2.895961             2.043539   
3    11417.0  5020.0       3.838446        3.253586             2.274303   
4    11132.0  4964.0       3.822925        3.242143             2.242546   

   green_score  
0    98.255319  
1    93.909091  
2    96.453608  
3   101.500000  
4    97.934066

In [84]:
# Saving the data to a CSV file
data_uk_merged.to_csv(os.path.join(file_path, "data_uk_merged_generation_demand.csv"), index=False)
print("Data saved to data_uk_merged_generation_demand.csv")

Data saved to data_uk_merged_generation_demand.csv


In [85]:
# Adding rolling and lag features in a dictionary since they will be used for different models
carbon_uk_shifted_for_ml_dict = {}
keys = ["30_min", "1_hour", "2 hour", "3_hours", "6_hours", "12_hours", "1_day", "2_day", "3_days", "5_days", "1_week", "2_week"]
for key in keys:

    # Create a copy of the dataframe with the last updates for each key
    carbon_uk_shifted = carbon['uk'].copy()

    if key == "30_min":
        pos = 0
    if key == "1_hour":
        pos = 1
    if key == "2 hour":
        pos = 2
    if key == "3_hours":
        pos = 3
    if key == "6_hours":
        pos = 4
    if key == "12_hours":
        pos = 5
    if key == "1_day":
        pos = 6
    if key == "2_day":
        pos = 7
    if key == "3_days":
        pos = 8
    if key == "5_days":
        pos = 9
    if key == "1_week":
        pos = 10
    if key == "2_week":
        pos = 11

    # Adding rolling features
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=6, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=8, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=12, pos=pos)

    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=5, pos=pos)

    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=3, pos=pos)

    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=6, pos=pos)
    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=9, pos=pos)

    carbon_uk_shifted = dc.create_rolling_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='years', window_size=1, pos=pos)

    # Adding lag features
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=6, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=12, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='hours', window_size=8, pos=pos)

    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='days', window_size=5, pos=pos)

    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='weeks', window_size=3, pos=pos)

    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=1, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=2, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=3, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=6, pos=pos)
    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='months', window_size=9, pos=pos)

    carbon_uk_shifted = dc.create_lag_features(carbon_uk_shifted, columns=["gas", "coal", "nuclear", "wind", "wind_emb", "hydro", "imports", "biomass", "other", "solar", "storage", "generation", "carbon_intensity", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"], type='years', window_size=1, pos=pos)

    # Drop the rows with NaN values
    length = len(carbon_uk_shifted)
    carbon_uk_shifted = carbon_uk_shifted.dropna()
    # Check if the length of the dataframe has changed
    if length != len(carbon_uk_shifted):
        print(f"For key {key}, length changed from {length} to {len(carbon_uk_shifted)}")

    # Drop the columns that are not needed. Only keeping the target and lag and rolling features
    carbon_uk_shifted = carbon_uk_shifted.drop(columns=["gas", "coal", "nuclear", "wind_emb", "hydro", "imports", "biomass", "other", "storage", "generation", "low_carbon", "zero_carbon", "renewable", "fossil", "low_vs_fossil", "zero_vs_fossil", "renewable_vs_fossil", "green_score"])

    # Merging the new featuresd with the original dataframe
    carbon_uk_shifted_for_ml_dict[key] = carbon_uk_shifted



For key 30_min, length changed from 110274 to 92753
For key 1_hour, length changed from 110274 to 92752
For key 2 hour, length changed from 110274 to 92750
For key 3_hours, length changed from 110274 to 92748
For key 6_hours, length changed from 110274 to 92742
For key 12_hours, length changed from 110274 to 92730
For key 1_day, length changed from 110274 to 92706
For key 2_day, length changed from 110274 to 92658
For key 3_days, length changed from 110274 to 92610
For key 5_days, length changed from 110274 to 92514
For key 1_week, length changed from 110274 to 92418
For key 2_week, length changed from 110274 to 92082


In [86]:
carbon['uk'] = 0

In [87]:
carbon_uk_shifted_for_ml_dict["30_min"].head()

wind  solar  carbon_intensity settlement_date  settlement_period  \
192817  5043.0    0.0             166.0      2020-01-01                  2   
192818  5030.0    0.0             164.0      2020-01-01                  3   
192819  4825.0    0.0             161.0      2020-01-01                  4   
192820  4689.0    0.0             158.0      2020-01-01                  5   
192821  4633.0    0.0             157.0      2020-01-01                  6   

        gas_rolling_1_hours_for_30_min  gas_rolling_std_1_hours_for_30_min  \
192817                          8014.0                          140.007143   
192818                          8169.0                          359.210245   
192819                          8231.5                          270.821897   
192820                          7771.0                          380.423448   
192821                          7262.5                          338.704148   

        gas_rolling_max_1_hours_for_30_min  \
192817                              8113.0   
192818                              8423.0   
192819                              8423.0   
192820                              8040.0   
192821                              7502.0   

        gas_rolling_min_1_hours_for_30_min  coal_rolling_1_hours_for_30_min  \
192817                              7915.0                            670.0   
192818                              7915.0                            670.0   
192819                              8040.0                            670.0   
192820                              7502.0                            670.0   
192821                              7023.0                            669.5   

        coal_rolling_std_1_hours_for_30_min  \
192817                             0.000000   
192818                             0.000000   
192819                             0.000000   
192820                             0.000000   
192821                             0.707107   

        coal_rolling_max_1_hours_for_30_min  \
192817                                670.0   
192818                                670.0   
192819                                670.0   
192820                                670.0   
192821                                670.0   

        coal_rolling_min_1_hours_for_30_min  \
192817                                670.0   
192818                                670.0   
192819                                670.0   
192820                                670.0   
192821                                669.0   

        nuclear_rolling_1_hours_for_30_min  \
192817                              6955.0   
192818                              6951.0   
192819                              6950.5   
192820                              6950.0   
192821                              6951.0   

        nuclear_rolling_std_1_hours_for_30_min  \
192817                                2.828427   
192818                                2.828427   
192819                                2.121320   
192820                                2.828427   
192821                                4.242641   

        nuclear_rolling_max_1_hours_for_30_min  \
192817                                  6957.0   
192818                                  6953.0   
192819                                  6952.0   
192820                                  6952.0   
192821                                  6954.0   

        nuclear_rolling_min_1_hours_for_30_min  \
192817                                  6953.0   
192818                                  6949.0   
192819                                  6949.0   
192820                                  6948.0   
192821                                  6948.0   

        wind_rolling_1_hours_for_30_min  wind_rolling_std_1_hours_for_30_min  \
192817                           5201.0                           278.600072   
192818                           5023.5                            27.577164   
192819                           5036.5            

In [88]:
carbon_uk_shifted_for_ml_dict["1_hour"].head()

wind  solar  carbon_intensity settlement_date  settlement_period  \
192818  5030.0    0.0             164.0      2020-01-01                  3   
192819  4825.0    0.0             161.0      2020-01-01                  4   
192820  4689.0    0.0             158.0      2020-01-01                  5   
192821  4633.0    0.0             157.0      2020-01-01                  6   
192822  4469.0    0.0             157.0      2020-01-01                  7   

        gas_rolling_1_hours_for_1_hour  gas_rolling_std_1_hours_for_1_hour  \
192818                          8014.0                          140.007143   
192819                          8169.0                          359.210245   
192820                          8231.5                          270.821897   
192821                          7771.0                          380.423448   
192822                          7262.5                          338.704148   

        gas_rolling_max_1_hours_for_1_hour  \
192818                              8113.0   
192819                              8423.0   
192820                              8423.0   
192821                              8040.0   
192822                              7502.0   

        gas_rolling_min_1_hours_for_1_hour  coal_rolling_1_hours_for_1_hour  \
192818                              7915.0                            670.0   
192819                              7915.0                            670.0   
192820                              8040.0                            670.0   
192821                              7502.0                            670.0   
192822                              7023.0                            669.5   

        coal_rolling_std_1_hours_for_1_hour  \
192818                             0.000000   
192819                             0.000000   
192820                             0.000000   
192821                             0.000000   
192822                             0.707107   

        coal_rolling_max_1_hours_for_1_hour  \
192818                                670.0   
192819                                670.0   
192820                                670.0   
192821                                670.0   
192822                                670.0   

        coal_rolling_min_1_hours_for_1_hour  \
192818                                670.0   
192819                                670.0   
192820                                670.0   
192821                                670.0   
192822                                669.0   

        nuclear_rolling_1_hours_for_1_hour  \
192818                              6955.0   
192819                              6951.0   
192820                              6950.5   
192821                              6950.0   
192822                              6951.0   

        nuclear_rolling_std_1_hours_for_1_hour  \
192818                                2.828427   
192819                                2.828427   
192820                                2.121320   
192821                                2.828427   
192822                                4.242641   

        nuclear_rolling_max_1_hours_for_1_hour  \
192818                                  6957.0   
192819                                  6953.0   
192820                                  6952.0   
192821                                  6952.0   
192822                                  6954.0   

        nuclear_rolling_min_1_hours_for_1_hour  \
192818                                  6953.0   
192819                                  6949.0   
192820                                  6949.0   
192821                                  6948.0   
192822                                  6948.0   

        wind_rolling_1_hours_for_1_hour  wind_rolling_std_1_hours_for_1_hour  \
192818                           5201.0                           278.600072   
192819                           5023.5                            27.577164   
192820                           5036.5            

In [89]:
# Check the dataframes for one key
ck.check(carbon_uk_shifted_for_ml_dict["30_min"])

Number of columns: 2000 and rows: 92753

Data types:
wind                                                 float64
solar                                                float64
carbon_intensity                                     float64
settlement_date                               datetime64[ns]
settlement_period                                      int32
                                                   ...      
fossil_lag_1_years_for_30_min                        float64
low_vs_fossil_lag_1_years_for_30_min                 float64
zero_vs_fossil_lag_1_years_for_30_min                float64
renewable_vs_fossil_lag_1_years_for_30_min           float64
green_score_lag_1_years_for_30_min                   float64
Length: 2000, dtype: object

Unique values count:
wind                                          15920
solar                                          9091
carbon_intensity                                314
settlement_date                                1933
settlement_period 

### Weather data

In [90]:
weather_path = os.path.join(file_path, "weather")

#### UK

- latitude: 54.727592
- longitude: -2.8458557
- elevation: 71.0
- utc_offset_seconds: 0
- timezone: GMT
- timezone_abbreviation: GMT

In [91]:
# Exploring the data
uk_weather_path = os.path.join(weather_path, "uk")

# Read the files in the directory
file_list = glob.glob(os.path.join(uk_weather_path, 'open-*.csv'))

# Initialize an empty dictionary to store the dataframes
weather = {}

# Loop through the files and read them into a dictionary
for file in file_list:

    # Read the file
    df = pd.read_csv(file)
    weather['uk'] = df

    print(f'Weather data loaded')

Weather data loaded


In [92]:
weather['uk'].head()

time  temperature_2m (°C)  relative_humidity_2m (%)  \
0  2019-01-01T00:00                  9.7                      87.0   
1  2019-01-01T01:00                  9.8                      87.0   
2  2019-01-01T02:00                  9.8                      89.0   
3  2019-01-01T03:00                  9.9                      89.0   
4  2019-01-01T04:00                  9.8                      92.0   

   apparent_temperature (°C)  precipitation (mm)  cloud_cover (%)  \
0                        5.4                 0.0             99.0   
1                        5.3                 0.0             99.0   
2                        5.6                 0.0            100.0   
3                        6.0                 0.1            100.0   
4                        6.2                 0.0             59.0   

   cloud_cover_low (%)  cloud_cover_mid (%)  wind_speed_10m (km/h)  \
0                 99.0                  0.0                   25.3   
1                 99.0                  0.0                   26.9   
2                100.0                  1.0                   25.6   
3                100.0                  4.0                   23.4   
4                 59.0                  0.0                   22.0   

   wind_speed_100m (km/h)  wind_direction_10m (°)  wind_direction_100m (°)  \
0                    41.9                   264.0                    266.0   
1                    43.4                   262.0                    265.0   
2                    41.8                   266.0                    269.0   
3                    38.6                   272.0                    274.0   
4                    35.7                   280.0                    282.0   

   wind_gusts_10m (km/h)  sunshine_duration (s)  direct_radiation (W/m²)  \
0                   50.0                    0.0                      0.0   
1                   50.8                    0.0                      0.0   
2                   51.1                    0.0                      0.0   
3                   48.6                    0.0                      0.0   
4                   44.6                    0.0                      0.0   

   shortwave_radiation (W/m²)  diffuse_radiation (W/m²)  \
0                         0.0                       0.0   
1                         0.0                       0.0   
2                         0.0                       0.0   
3                         0.0                       0.0   
4                         0.0                       0.0   

   shortwave_radiation_instant (W/m²)  diffuse_radiation_instant (W/m²)  \
0                                 0.0                               0.0   
1                                 0.0                               0.0   
2                                 0.0                               0.0   
3                                 0.0                               0.0   
4                                 0.0                               0.0   

   global_tilted_irradiance (W/m²)  global_tilted_irradiance_instant (W/m²)  \
0                              0.0                                      0.0   
1                              0.0                                      0.0   
2                              0.0                                      0.0   
3                              0.0                                      0.0   
4                              0.0                                      0.0   

   direct_normal_irradiance (W/m²)  terrestrial_radiation (W/m²)  
0                              0.0                           0.0  
1                              0.0                           0.0  
2                              0.0                           0.0  
3                              0.0                           0.0  
4                              0.0                           0.0

In [93]:
# Snake case columns
for key, value in weather.items():
    # Rename the columns
    weather[key] = dc.snake(value)

In [94]:
# Let's convert datetime to datetime format
for key, value in weather.items():
    # Rename the columns
    weather[key] = dc.convert_to_datetime(value, columns=["time"])

In [95]:
weather['uk'].head()

time  temperature_2m_°c  relative_humidity_2m_%  \
0 2019-01-01 00:00:00                9.7                    87.0   
1 2019-01-01 01:00:00                9.8                    87.0   
2 2019-01-01 02:00:00                9.8                    89.0   
3 2019-01-01 03:00:00                9.9                    89.0   
4 2019-01-01 04:00:00                9.8                    92.0   

   apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
0                      5.4               0.0           99.0   
1                      5.3               0.0           99.0   
2                      5.6               0.0          100.0   
3                      6.0               0.1          100.0   
4                      6.2               0.0           59.0   

   cloud_cover_low_%  cloud_cover_mid_%  wind_speed_10m_km/h  \
0               99.0                0.0                 25.3   
1               99.0                0.0                 26.9   
2              100.0                1.0                 25.6   
3              100.0                4.0                 23.4   
4               59.0                0.0                 22.0   

   wind_speed_100m_km/h  wind_direction_10m_°  wind_direction_100m_°  \
0                  41.9                 264.0                  266.0   
1                  43.4                 262.0                  265.0   
2                  41.8                 266.0                  269.0   
3                  38.6                 272.0                  274.0   
4                  35.7                 280.0                  282.0   

   wind_gusts_10m_km/h  sunshine_duration_s  direct_radiation_w/m²  \
0                 50.0                  0.0                    0.0   
1                 50.8                  0.0                    0.0   
2                 51.1                  0.0                    0.0   
3                 48.6                  0.0                    0.0   
4                 44.6                  0.0                    0.0   

   shortwave_radiation_w/m²  diffuse_radiation_w/m²  \
0                       0.0                     0.0   
1                       0.0                     0.0   
2                       0.0                     0.0   
3                       0.0                     0.0   
4                       0.0                     0.0   

   shortwave_radiation_instant_w/m²  diffuse_radiation_instant_w/m²  \
0                               0.0                             0.0   
1                               0.0                             0.0   
2                               0.0                             0.0   
3                               0.0                             0.0   
4                               0.0                             0.0   

   global_tilted_irradiance_w/m²  global_tilted_irradiance_instant_w/m²  \
0                            0.0                                    0.0   
1                            0.0                                    0.0   
2                            0.0                                    0.0   
3                            0.0                                    0.0   
4                            0.0                                    0.0   

   direct_normal_irradiance_w/m²  terrestrial_radiation_w/m²  
0                            0.0                         0.0  
1                            0.0                         0.0  
2                            0.0                         0.0  
3                            0.0                         0.0  
4                            0.0                         0.0

In [96]:
weather['uk'].tail()

time  temperature_2m_°c  relative_humidity_2m_%  \
55267 2025-04-21 19:00:00                NaN                     NaN   
55268 2025-04-21 20:00:00                NaN                     NaN   
55269 2025-04-21 21:00:00                NaN                     NaN   
55270 2025-04-21 22:00:00                NaN                     NaN   
55271 2025-04-21 23:00:00                NaN                     NaN   

       apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
55267                      NaN               NaN            NaN   
55268                      NaN               NaN            NaN   
55269                      NaN               NaN            NaN   
55270                      NaN               NaN            NaN   
55271                      NaN               NaN            NaN   

       cloud_cover_low_%  cloud_cover_mid_%  wind_speed_10m_km/h  \
55267                NaN                NaN                  NaN   
55268                NaN                NaN                  NaN   
55269                NaN                NaN                  NaN   
55270                NaN                NaN                  NaN   
55271                NaN                NaN                  NaN   

       wind_speed_100m_km/h  wind_direction_10m_°  wind_direction_100m_°  \
55267                   NaN                   NaN                    NaN   
55268                   NaN                   NaN                    NaN   
55269                   NaN                   NaN                    NaN   
55270                   NaN                   NaN                    NaN   
55271                   NaN                   NaN                    NaN   

       wind_gusts_10m_km/h  sunshine_duration_s  direct_radiation_w/m²  \
55267                  NaN                  NaN                    NaN   
55268                  NaN                  NaN                    NaN   
55269                  NaN                  NaN                    NaN   
55270                  NaN                  NaN                    NaN   
55271                  NaN                  NaN                    NaN   

       shortwave_radiation_w/m²  diffuse_radiation_w/m²  \
55267                       NaN                     NaN   
55268                       NaN                     NaN   
55269                       NaN                     NaN   
55270                       NaN                     NaN   
55271                       NaN                     NaN   

       shortwave_radiation_instant_w/m²  diffuse_radiation_instant_w/m²  \
55267                               NaN                             NaN   
55268                               NaN                             NaN   
55269                               NaN                             NaN   
55270                               NaN                             NaN   
55271                               NaN                             NaN   

       global_tilted_irradiance_w/m²  global_tilted_irradiance_instant_w/m²  \
55267                            NaN                                    NaN   
55268                            NaN                                    NaN   
55269                            NaN                                    NaN   
55270                            NaN                                    NaN   
55271                            NaN                                    NaN   

       direct_normal_irradiance_w/m²  terrestrial_radiation_w/m²  
55267                            NaN                       165.9  
55268                            NaN                        23.4  
55269                            NaN                         0.0  
55270                            NaN                         0.0  
55271                            NaN                         0.0

In [97]:
# Adding zone info to deal with DST entries
from zoneinfo import ZoneInfo
weather['uk']["time"] = weather['uk']["time"].dt.tz_localize('UTC')
weather['uk']["time_london"] = weather['uk']["time"].dt.tz_convert('Europe/London')

In [98]:
# Extracting necessary columns
weather = dc.extract_columns(weather,["time_london", "temperature_2m_°c", "relative_humidity_2m_%", "apparent_temperature_°c", "precipitation_mm", "cloud_cover_%", \
                                      "wind_speed_10m_km/h", "wind_speed_100m_km/h", "wind_direction_10m_°", "wind_direction_100m_°", "global_tilted_irradiance_w/m²", \
                                        "direct_radiation_w/m²", "terrestrial_radiation_w/m²", "shortwave_radiation_w/m²", "direct_normal_irradiance_w/m²", "diffuse_radiation_w/m²"])

Columns ['time_london', 'temperature_2m_°c', 'relative_humidity_2m_%', 'apparent_temperature_°c', 'precipitation_mm', 'cloud_cover_%', 'wind_speed_10m_km/h', 'wind_speed_100m_km/h', 'wind_direction_10m_°', 'wind_direction_100m_°', 'global_tilted_irradiance_w/m²', 'direct_radiation_w/m²', 'terrestrial_radiation_w/m²', 'shortwave_radiation_w/m²', 'direct_normal_irradiance_w/m²', 'diffuse_radiation_w/m²'] extracted from data uk


In [99]:
weather['uk'].tail()

time_london  temperature_2m_°c  relative_humidity_2m_%  \
55267 2025-04-21 20:00:00+01:00                NaN                     NaN   
55268 2025-04-21 21:00:00+01:00                NaN                     NaN   
55269 2025-04-21 22:00:00+01:00                NaN                     NaN   
55270 2025-04-21 23:00:00+01:00                NaN                     NaN   
55271 2025-04-22 00:00:00+01:00                NaN                     NaN   

       apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
55267                      NaN               NaN            NaN   
55268                      NaN               NaN            NaN   
55269                      NaN               NaN            NaN   
55270                      NaN               NaN            NaN   
55271                      NaN               NaN            NaN   

       wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
55267                  NaN                   NaN                   NaN   
55268                  NaN                   NaN                   NaN   
55269                  NaN                   NaN                   NaN   
55270                  NaN                   NaN                   NaN   
55271                  NaN                   NaN                   NaN   

       wind_direction_100m_°  global_tilted_irradiance_w/m²  \
55267                    NaN                            NaN   
55268                    NaN                            NaN   
55269                    NaN                            NaN   
55270                    NaN                            NaN   
55271                    NaN                            NaN   

       direct_radiation_w/m²  terrestrial_radiation_w/m²  \
55267                    NaN                       165.9   
55268                    NaN                        23.4   
55269                    NaN                         0.0   
55270                    NaN                         0.0   
55271                    NaN                         0.0   

       shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
55267                       NaN                            NaN   
55268                       NaN                            NaN   
55269                       NaN                            NaN   
55270                       NaN                            NaN   
55271                       NaN                            NaN   

       diffuse_radiation_w/m²  
55267                     NaN  
55268                     NaN  
55269                     NaN  
55270                     NaN  
55271                     NaN

In [100]:
# Removing some rows with missing data at the tail
length = len(weather['uk'])
weather['uk'] = weather['uk'].dropna()
if length != len(weather['uk']):
    print(f"Length changed from {length} to {len(weather['uk'])}")

Length changed from 55272 to 55249


In [101]:
weather['uk'].tail()

time_london  temperature_2m_°c  relative_humidity_2m_%  \
55244 2025-04-20 21:00:00+01:00                9.1                    76.0   
55245 2025-04-20 22:00:00+01:00                8.0                    81.0   
55246 2025-04-20 23:00:00+01:00                7.5                    84.0   
55247 2025-04-21 00:00:00+01:00                6.7                    88.0   
55248 2025-04-21 01:00:00+01:00                6.2                    89.0   

       apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
55244                      5.7               0.0           19.0   
55245                      4.7               0.0           50.0   
55246                      4.1               0.0           48.0   
55247                      3.1               0.0           45.0   
55248                      2.8               0.0          100.0   

       wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
55244                 14.8                  28.8                 137.0   
55245                 13.9                  27.4                 138.0   
55246                 14.7                  27.8                 137.0   
55247                 15.5                  28.9                 142.0   
55248                 14.5                  27.6                 146.0   

       wind_direction_100m_°  global_tilted_irradiance_w/m²  \
55244                  137.0                            3.0   
55245                  135.0                            0.0   
55246                  136.0                            0.0   
55247                  140.0                            0.0   
55248                  143.0                            0.0   

       direct_radiation_w/m²  terrestrial_radiation_w/m²  \
55244                    0.0                        20.5   
55245                    0.0                         0.0   
55246                    0.0                         0.0   
55247                    0.0                         0.0   
55248                    0.0                         0.0   

       shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
55244                       3.0                            0.0   
55245                       0.0                            0.0   
55246                       0.0                            0.0   
55247                       0.0                            0.0   
55248                       0.0                            0.0   

       diffuse_radiation_w/m²  
55244                     3.0  
55245                     0.0  
55246                     0.0  
55247                     0.0  
55248                     0.0

In [102]:
# Adding and removing rows at the DST chnages
weather['uk'] = dc.check_time_increase_in_weather(weather['uk'], "time_london")

🕑 Added missing row for: 2019-03-31 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2019-10-27 01:00:00 → averaged values
🕑 Added missing row for: 2020-03-29 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2020-10-25 01:00:00 → averaged values
🕑 Added missing row for: 2021-03-28 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2021-10-31 01:00:00 → averaged values
🕑 Added missing row for: 2022-03-27 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2022-10-30 01:00:00 → averaged values
🕑 Added missing row for: 2023-03-26 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2023-10-29 01:00:00 → averaged values
🕑 Added missing row for: 2024-03-31 01:00:00 → interpolated values
⚠️ Removed duplicate for time: 2024-10-27 01:00:00 → averaged values
🕑 Added missing row for: 2025-03-30 01:00:00 → interpolated values


In [103]:
# The data is in 1 h intervals, so we need to forward fill the data to get the values for each settlement period
# Since resample dont resample beyond the last date, we need to add a point beyond the last time value, so we have the resample for the last value
# This will be erased after the resample
weather['uk'] = dc.resample(weather['uk'], col='time_london')
weather['uk'] = weather['uk'].rename(columns={"time_london": "time"})

In [104]:
weather['uk'].head()

time  temperature_2m_°c  relative_humidity_2m_%  \
0 2019-01-01 00:00:00                9.7                    87.0   
1 2019-01-01 00:30:00                9.7                    87.0   
2 2019-01-01 01:00:00                9.8                    87.0   
3 2019-01-01 01:30:00                9.8                    87.0   
4 2019-01-01 02:00:00                9.8                    89.0   

   apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
0                      5.4               0.0           99.0   
1                      5.4               0.0           99.0   
2                      5.3               0.0           99.0   
3                      5.3               0.0           99.0   
4                      5.6               0.0          100.0   

   wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
0                 25.3                  41.9                 264.0   
1                 25.3                  41.9                 264.0   
2                 26.9                  43.4                 262.0   
3                 26.9                  43.4                 262.0   
4                 25.6                  41.8                 266.0   

   wind_direction_100m_°  global_tilted_irradiance_w/m²  \
0                  266.0                            0.0   
1                  266.0                            0.0   
2                  265.0                            0.0   
3                  265.0                            0.0   
4                  269.0                            0.0   

   direct_radiation_w/m²  terrestrial_radiation_w/m²  \
0                    0.0                         0.0   
1                    0.0                         0.0   
2                    0.0                         0.0   
3                    0.0                         0.0   
4                    0.0                         0.0   

   shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
0                       0.0                            0.0   
1                       0.0                            0.0   
2                       0.0                            0.0   
3                       0.0                            0.0   
4                       0.0                            0.0   

   diffuse_radiation_w/m²  
0                     0.0  
1                     0.0  
2                     0.0  
3                     0.0  
4                     0.0

In [105]:
# Check the data types, missing values, and duplicates
ck.check(weather['uk'])

Number of columns: 16 and rows: 110500

Data types:
time                             datetime64[ns]
temperature_2m_°c                       float64
relative_humidity_2m_%                  float64
apparent_temperature_°c                 float64
precipitation_mm                        float64
cloud_cover_%                           float64
wind_speed_10m_km/h                     float64
wind_speed_100m_km/h                    float64
wind_direction_10m_°                    float64
wind_direction_100m_°                   float64
global_tilted_irradiance_w/m²           float64
direct_radiation_w/m²                   float64
terrestrial_radiation_w/m²              float64
shortwave_radiation_w/m²                float64
direct_normal_irradiance_w/m²           float64
diffuse_radiation_w/m²                  float64
dtype: object

Unique values count:
time                             110500
temperature_2m_°c                   357
relative_humidity_2m_%               81
apparent_temperature_°c 

In [106]:
weather['uk'].tail()

time  temperature_2m_°c  relative_humidity_2m_%  \
110495 2025-04-20 23:30:00                7.5                    84.0   
110496 2025-04-21 00:00:00                6.7                    88.0   
110497 2025-04-21 00:30:00                6.7                    88.0   
110498 2025-04-21 01:00:00                6.2                    89.0   
110499 2025-04-21 01:30:00                6.2                    89.0   

        apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
110495                      4.1               0.0           48.0   
110496                      3.1               0.0           45.0   
110497                      3.1               0.0           45.0   
110498                      2.8               0.0          100.0   
110499                      2.8               0.0          100.0   

        wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
110495                 14.7                  27.8                 137.0   
110496                 15.5                  28.9                 142.0   
110497                 15.5                  28.9                 142.0   
110498                 14.5                  27.6                 146.0   
110499                 14.5                  27.6                 146.0   

        wind_direction_100m_°  global_tilted_irradiance_w/m²  \
110495                  136.0                            0.0   
110496                  140.0                            0.0   
110497                  140.0                            0.0   
110498                  143.0                            0.0   
110499                  143.0                            0.0   

        direct_radiation_w/m²  terrestrial_radiation_w/m²  \
110495                    0.0                         0.0   
110496                    0.0                         0.0   
110497                    0.0                         0.0   
110498                    0.0                         0.0   
110499                    0.0                         0.0   

        shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
110495                       0.0                            0.0   
110496                       0.0                            0.0   
110497                       0.0                            0.0   
110498                       0.0                            0.0   
110499                       0.0                            0.0   

        diffuse_radiation_w/m²  
110495                     0.0  
110496                     0.0  
110497                     0.0  
110498                     0.0  
110499                     0.0

In [107]:
# Extracting setellment period and settlement date from datetime
weather['uk'] = dc.extract_settlement_period_and_date(weather['uk'], "time")

In [108]:
weather['uk'].head()

temperature_2m_°c  relative_humidity_2m_%  apparent_temperature_°c  \
0                9.7                    87.0                      5.4   
1                9.7                    87.0                      5.4   
2                9.8                    87.0                      5.3   
3                9.8                    87.0                      5.3   
4                9.8                    89.0                      5.6   

   precipitation_mm  cloud_cover_%  wind_speed_10m_km/h  wind_speed_100m_km/h  \
0               0.0           99.0                 25.3                  41.9   
1               0.0           99.0                 25.3                  41.9   
2               0.0           99.0                 26.9                  43.4   
3               0.0           99.0                 26.9                  43.4   
4               0.0          100.0                 25.6                  41.8   

   wind_direction_10m_°  wind_direction_100m_°  global_tilted_irradiance_w/m²  \
0                 264.0                  266.0                            0.0   
1                 264.0                  266.0                            0.0   
2                 262.0                  265.0                            0.0   
3                 262.0                  265.0                            0.0   
4                 266.0                  269.0                            0.0   

   direct_radiation_w/m²  terrestrial_radiation_w/m²  \
0                    0.0                         0.0   
1                    0.0                         0.0   
2                    0.0                         0.0   
3                    0.0                         0.0   
4                    0.0                         0.0   

   shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
0                       0.0                            0.0   
1                       0.0                            0.0   
2                       0.0                            0.0   
3                       0.0                            0.0   
4                       0.0                            0.0   

   diffuse_radiation_w/m² settlement_date  settlement_period  
0                     0.0      2019-01-01                  1  
1                     0.0      2019-01-01                  2  
2                     0.0      2019-01-01                  3  
3                     0.0      2019-01-01                  4  
4                     0.0      2019-01-01                  5

In [109]:
ck.check(weather['uk'])

Number of columns: 17 and rows: 110500

Data types:
temperature_2m_°c                       float64
relative_humidity_2m_%                  float64
apparent_temperature_°c                 float64
precipitation_mm                        float64
cloud_cover_%                           float64
wind_speed_10m_km/h                     float64
wind_speed_100m_km/h                    float64
wind_direction_10m_°                    float64
wind_direction_100m_°                   float64
global_tilted_irradiance_w/m²           float64
direct_radiation_w/m²                   float64
terrestrial_radiation_w/m²              float64
shortwave_radiation_w/m²                float64
direct_normal_irradiance_w/m²           float64
diffuse_radiation_w/m²                  float64
settlement_date                  datetime64[ns]
settlement_period                         int32
dtype: object

Unique values count:
temperature_2m_°c                  357
relative_humidity_2m_%              81
apparent_temperatu

In [110]:
# Saving the data to a CSV file
weather['uk'].to_csv(os.path.join(uk_weather_path, "uk_weather_fix.csv"), index=False)
print("Data saved to uk_weather_fix.csv")

Data saved to uk_weather_fix.csv


In [111]:
# Modify the date column to include the time
weather_with_time = dc.add_time(weather['uk'], "settlement_date")

In [112]:
weather_with_time.head()

temperature_2m_°c  relative_humidity_2m_%  apparent_temperature_°c  \
0                9.7                    87.0                      5.4   
1                9.7                    87.0                      5.4   
2                9.8                    87.0                      5.3   
3                9.8                    87.0                      5.3   
4                9.8                    89.0                      5.6   

   precipitation_mm  cloud_cover_%  wind_speed_10m_km/h  wind_speed_100m_km/h  \
0               0.0           99.0                 25.3                  41.9   
1               0.0           99.0                 25.3                  41.9   
2               0.0           99.0                 26.9                  43.4   
3               0.0           99.0                 26.9                  43.4   
4               0.0          100.0                 25.6                  41.8   

   wind_direction_10m_°  wind_direction_100m_°  global_tilted_irradiance_w/m²  \
0                 264.0                  266.0                            0.0   
1                 264.0                  266.0                            0.0   
2                 262.0                  265.0                            0.0   
3                 262.0                  265.0                            0.0   
4                 266.0                  269.0                            0.0   

   direct_radiation_w/m²  terrestrial_radiation_w/m²  \
0                    0.0                         0.0   
1                    0.0                         0.0   
2                    0.0                         0.0   
3                    0.0                         0.0   
4                    0.0                         0.0   

   shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
0                       0.0                            0.0   
1                       0.0                            0.0   
2                       0.0                            0.0   
3                       0.0                            0.0   
4                       0.0                            0.0   

   diffuse_radiation_w/m²     settlement_date  settlement_period  
0                     0.0 2019-01-01 00:00:00                  1  
1                     0.0 2019-01-01 00:30:00                  2  
2                     0.0 2019-01-01 01:00:00                  3  
3                     0.0 2019-01-01 01:30:00                  4  
4                     0.0 2019-01-01 02:00:00                  5

In [113]:
# Merging with demand and generation data
data_uk_merged_with_weather = pd.merge(data_uk_merged, weather_with_time, how="left", left_on=["settlement_date", "settlement_period"], right_on=["settlement_date", "settlement_period"])
lenght = len(data_uk_merged_with_weather)
data_uk_merged_with_weather = dc.drop_nan_rows(data_uk_merged_with_weather)
if lenght != len(data_uk_merged_with_weather):
    print(f"Length changed from {lenght} to {len(data_uk_merged_with_weather)}")

# Modify the date column to include the time
data_uk_merged_with_weather = dc.add_time(data_uk_merged_with_weather, "settlement_date")

data_uk_merged_with_weather = data_uk_merged_with_weather.sort_values(by=["settlement_date", "settlement_period"])
data_uk_merged_with_weather = data_uk_merged_with_weather.reset_index(drop=True)
data_uk_merged_with_weather["is_bank_holiday"] = data_uk_merged_with_weather["is_bank_holiday"].astype(int)
data_uk_merged_with_weather.head()

Number of rows dropped due to NaN values: 0


settlement_date  settlement_period     nd    tsd  is_bank_holiday  \
0 2019-01-01 00:00:00                  1  23808  25291                1   
1 2019-01-01 00:30:00                  2  24402  25720                1   
2 2019-01-01 01:00:00                  3  24147  25495                1   
3 2019-01-01 01:30:00                  4  23197  24590                1   
4 2019-01-01 02:00:00                  5  22316  24346                1   

      gas  coal  nuclear    wind  wind_emb  hydro  imports  biomass  other  \
0  5853.0   0.0   6924.0  9236.0    2031.0    405   1734.0   1052.0   64.0   
1  6292.0   0.0   6838.0  9297.0    1997.0    388   1750.0   1040.0   63.0   
2  5719.0   0.0   6834.0  9356.0    1959.0    372   2092.0   1026.0   64.0   
3  5020.0   0.0   6830.0  9135.0    1914.0    368   2104.0   1022.0   63.0   
4  4964.0   0.0   6827.0  8912.0    1865.0    355   2203.0   1018.0   63.0   

   solar  storage  generation  carbon_intensity  low_carbon  zero_carbon  \
0    0.0        0     27299.0              94.0     19648.0      16565.0   
1    0.0       24     27689.0              99.0     19584.0      16547.0   
2    0.0        0     27422.0              97.0     19547.0      16562.0   
3    0.0        0     26456.0              90.0     19269.0      16333.0   
4    0.0        0     26207.0              91.0     18977.0      16094.0   

   renewable  fossil  low_vs_fossil  zero_vs_fossil  renewable_vs_fossil  \
0    11672.0  5853.0       3.356911        2.830173             1.994191   
1    11706.0  6292.0       3.112524        2.629847             1.860458   
2    11687.0  5719.0       3.417905        2.895961             2.043539   
3    11417.0  5020.0       3.838446        3.253586             2.274303   
4    11132.0  4964.0       3.822925        3.242143             2.242546   

   green_score  temperature_2m_°c  relative_humidity_2m_%  \
0    98.255319                9.7                    87.0   
1    93.909091                9.7                    87.0   
2    96.453608                9.8                    87.0   
3   101.500000                9.8                    87.0   
4    97.934066                9.8                    89.0   

   apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
0                      5.4               0.0           99.0   
1                      5.4               0.0           99.0   
2                      5.3               0.0           99.0   
3                      5.3               0.0           99.0   
4                      5.6               0.0          100.0   

   wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
0                 25.3                  41.9                 264.0   
1                 25.3                  41.9                 264.0   
2                 26.9                  43.4                 262.0   
3                 26.9                  43.4                 262.0   
4                 25.6                  41.8                 266.0   

   wind_direction_100m_°  global_tilted_irradiance_w/m²  \
0                  266.0                            0.0   
1                  266.0                            0.0   
2                  265.0                            0.0   
3                  265.0                            0.0   
4                  269.0                            0.0   

   direct_radiation_w/m²  terrestrial_radiation_w/m²  \
0                    0.0                         0.0   
1                    0.0                         0.0   
2                    0.0                         0.0   
3                    0.0                         0.0   
4                    0.0                         0.0   

   shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
0                       0.0                            0.0   
1                       0.0                            0.0   
2                       0.0                            0.0   
3                       0.0                            0.0   
4  

In [114]:
# Let's split the date into separate columns for year, month, day of week and day
data_uk_merged_with_weather = dc.preprocess_datetime(data_uk_merged_with_weather, "settlement_date")
data_uk_merged_with_weather = dc.one_hot_encode(data_uk_merged_with_weather, 'season')
data_uk_merged_with_weather.head()

settlement_date  settlement_period     nd    tsd  is_bank_holiday  \
0 2019-01-01 00:00:00                  1  23808  25291                1   
1 2019-01-01 00:30:00                  2  24402  25720                1   
2 2019-01-01 01:00:00                  3  24147  25495                1   
3 2019-01-01 01:30:00                  4  23197  24590                1   
4 2019-01-01 02:00:00                  5  22316  24346                1   

      gas  coal  nuclear    wind  wind_emb  hydro  imports  biomass  other  \
0  5853.0   0.0   6924.0  9236.0    2031.0    405   1734.0   1052.0   64.0   
1  6292.0   0.0   6838.0  9297.0    1997.0    388   1750.0   1040.0   63.0   
2  5719.0   0.0   6834.0  9356.0    1959.0    372   2092.0   1026.0   64.0   
3  5020.0   0.0   6830.0  9135.0    1914.0    368   2104.0   1022.0   63.0   
4  4964.0   0.0   6827.0  8912.0    1865.0    355   2203.0   1018.0   63.0   

   solar  storage  generation  carbon_intensity  low_carbon  zero_carbon  \
0    0.0        0     27299.0              94.0     19648.0      16565.0   
1    0.0       24     27689.0              99.0     19584.0      16547.0   
2    0.0        0     27422.0              97.0     19547.0      16562.0   
3    0.0        0     26456.0              90.0     19269.0      16333.0   
4    0.0        0     26207.0              91.0     18977.0      16094.0   

   renewable  fossil  low_vs_fossil  zero_vs_fossil  renewable_vs_fossil  \
0    11672.0  5853.0       3.356911        2.830173             1.994191   
1    11706.0  6292.0       3.112524        2.629847             1.860458   
2    11687.0  5719.0       3.417905        2.895961             2.043539   
3    11417.0  5020.0       3.838446        3.253586             2.274303   
4    11132.0  4964.0       3.822925        3.242143             2.242546   

   green_score  temperature_2m_°c  relative_humidity_2m_%  \
0    98.255319                9.7                    87.0   
1    93.909091                9.7                    87.0   
2    96.453608                9.8                    87.0   
3   101.500000                9.8                    87.0   
4    97.934066                9.8                    89.0   

   apparent_temperature_°c  precipitation_mm  cloud_cover_%  \
0                      5.4               0.0           99.0   
1                      5.4               0.0           99.0   
2                      5.3               0.0           99.0   
3                      5.3               0.0           99.0   
4                      5.6               0.0          100.0   

   wind_speed_10m_km/h  wind_speed_100m_km/h  wind_direction_10m_°  \
0                 25.3                  41.9                 264.0   
1                 25.3                  41.9                 264.0   
2                 26.9                  43.4                 262.0   
3                 26.9                  43.4                 262.0   
4                 25.6                  41.8                 266.0   

   wind_direction_100m_°  global_tilted_irradiance_w/m²  \
0                  266.0                            0.0   
1                  266.0                            0.0   
2                  265.0                            0.0   
3                  265.0                            0.0   
4                  269.0                            0.0   

   direct_radiation_w/m²  terrestrial_radiation_w/m²  \
0                    0.0                         0.0   
1                    0.0                         0.0   
2                    0.0                         0.0   
3                    0.0                         0.0   
4                    0.0                         0.0   

   shortwave_radiation_w/m²  direct_normal_irradiance_w/m²  \
0                       0.0                            0.0   
1                       0.0                            0.0   
2                       0.0                            0.0   
3                       0.0                            0.0   
4  

In [115]:
ck.check(data_uk_merged_with_weather)

Number of columns: 49 and rows: 110263

Data types:
settlement_date                  datetime64[ns]
settlement_period                         int64
nd                                        int64
tsd                                       int64
is_bank_holiday                           int64
gas                                     float64
coal                                    float64
nuclear                                 float64
wind                                    float64
wind_emb                                float64
hydro                                     int64
imports                                 float64
biomass                                 float64
other                                   float64
solar                                   float64
storage                                   int64
generation                              float64
carbon_intensity                        float64
low_carbon                              float64
zero_carbon                         

In [116]:
# Saving the data to csv file
data_uk_merged_with_weather.to_csv(os.path.join(file_path, "uk_full_for_eda.csv"), index=False)
print("Data saved to uk_full_for_eda.csv")

Data saved to uk_full_for_eda.csv


In [117]:
data_uk_merged_with_weather = 0
weather_with_time = 0

In [118]:
# Adding rolling and lag features in a dictionary since they will be used for different models
weather_uk_shifted_for_ml_dict = {}
keys = ["30_min", "1_hour", "2 hour", "3_hours", "6_hours", "12_hours", "1_day", "2_day", "3_days", "5_days", "1_week", "2_week"]
for key in keys:

    # Create a copy of the dataframe with the last updates for each key
    weather_uk_shifted = weather['uk'].copy()

    if key == "30_min":
        pos = 0
    if key == "1_hour":
        pos = 1
    if key == "2 hour":
        pos = 2
    if key == "3_hours":
        pos = 3
    if key == "6_hours":
        pos = 4
    if key == "12_hours":
        pos = 5
    if key == "1_day":
        pos = 6
    if key == "2_day":
        pos = 7
    if key == "3_days":
        pos = 8
    if key == "5_days":
        pos = 9
    if key == "1_week":
        pos = 10
    if key == "2_week":
        pos = 11

    columns_to_use = [
        "temperature_2m_°c", "relative_humidity_2m_%", "apparent_temperature_°c",
        "precipitation_mm", "cloud_cover_%", "wind_speed_10m_km/h",
        "wind_speed_100m_km/h", "wind_direction_10m_°", "wind_direction_100m_°",
        "global_tilted_irradiance_w/m²", "direct_radiation_w/m²",
        "terrestrial_radiation_w/m²", "shortwave_radiation_w/m²",
        "direct_normal_irradiance_w/m²", "diffuse_radiation_w/m²"
    ]

    # Adding rolling features
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=6, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=8, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=12, pos=pos)

    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=5, pos=pos)

    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=3, pos=pos)

    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=6, pos=pos)
    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=9, pos=pos)

    weather_uk_shifted = dc.create_rolling_features(weather_uk_shifted, columns=columns_to_use, type='years', window_size=1, pos=pos)

    # Adding lag features
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=6, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=12, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='hours', window_size=8, pos=pos)

    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='days', window_size=5, pos=pos)

    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='weeks', window_size=3, pos=pos)

    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=1, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=2, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=3, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=6, pos=pos)
    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='months', window_size=9, pos=pos)

    weather_uk_shifted = dc.create_lag_features(weather_uk_shifted, columns=columns_to_use, type='years', window_size=1, pos=pos)

    # Drop the rows with NaN values
    length = len(weather_uk_shifted)
    weather_uk_shifted = weather_uk_shifted.dropna()
    # Check if the length of the dataframe has changed
    if length != len(weather_uk_shifted):
        print(f"For key {key}, length changed from {length} to {len(weather_uk_shifted)}")

    # Drop the columns that are not needed. Only keeping the target and lag and rolling features
    weather_uk_shifted = weather_uk_shifted.drop(columns=columns_to_use)

    # Merging the new featuresd with the original dataframe
    weather_uk_shifted_for_ml_dict[key] = weather_uk_shifted



For key 30_min, length changed from 110500 to 92979
For key 1_hour, length changed from 110500 to 92978
For key 2 hour, length changed from 110500 to 92976
For key 3_hours, length changed from 110500 to 92974
For key 6_hours, length changed from 110500 to 92968
For key 12_hours, length changed from 110500 to 92956
For key 1_day, length changed from 110500 to 92932
For key 2_day, length changed from 110500 to 92884
For key 3_days, length changed from 110500 to 92836
For key 5_days, length changed from 110500 to 92740
For key 1_week, length changed from 110500 to 92644
For key 2_week, length changed from 110500 to 92308


In [119]:
weather['uk'] = 0

In [120]:
weather_uk_shifted_for_ml_dict["30_min"].head()

settlement_date  settlement_period  \
17521      2020-01-01                  2   
17522      2020-01-01                  3   
17523      2020-01-01                  4   
17524      2020-01-01                  5   
17525      2020-01-01                  6   

       temperature_2m_°c_rolling_1_hours_for_30_min  \
17521                                          3.15   
17522                                          2.70   
17523                                          2.90   
17524                                          3.10   
17525                                          3.40   

       temperature_2m_°c_rolling_std_1_hours_for_30_min  \
17521                                          0.636396   
17522                                          0.000000   
17523                                          0.282843   
17524                                          0.000000   
17525                                          0.424264   

       temperature_2m_°c_rolling_max_1_hours_for_30_min  \
17521                                               3.6   
17522                                               2.7   
17523                                               3.1   
17524                                               3.1   
17525                                               3.7   

       temperature_2m_°c_rolling_min_1_hours_for_30_min  \
17521                                               2.7   
17522                                               2.7   
17523                                               2.7   
17524                                               3.1   
17525                                               3.1   

       relative_humidity_2m_%_rolling_1_hours_for_30_min  \
17521                                               95.0   
17522                                               95.0   
17523                                               95.0   
17524                                               95.0   
17525                                               96.0   

       relative_humidity_2m_%_rolling_std_1_hours_for_30_min  \
17521                                           0.000000       
17522                                           0.000000       
17523                                           0.000000       
17524                                           0.000000       
17525                                           1.414214       

       relative_humidity_2m_%_rolling_max_1_hours_for_30_min  \
17521                                               95.0       
17522                                               95.0       
17523                                               95.0       
17524                                               95.0       
17525                                               97.0       

       relative_humidity_2m_%_rolling_min_1_hours_for_30_min  \
17521                                               95.0       
17522                                               95.0       
17523                                               95.0       
17524                                               95.0       
17525                                               95.0       

       apparent_temperature_°c_rolling_1_hours_for_30_min  \
17521                                               0.15    
17522                                               0.00    
17523                                               0.40    
17524                                               0.80    
17525                                               1.00    

       apparent_temperature_°c_rolling_std_1_hours_for_30_min  \
17521                                           0.212132        
17522                                           0.000000        
17523                                           0.565685        
17524                                           0.000000        
17525                                           0.282843        

       apparent_temperature_°c_rolling_max_1_hours_for_30_min  \
17521 

In [121]:
weather_uk_shifted_for_ml_dict["30_min"].tail()

settlement_date  settlement_period  \
110495      2025-04-20                 48   
110496      2025-04-21                  1   
110497      2025-04-21                  2   
110498      2025-04-21                  3   
110499      2025-04-21                  4   

        temperature_2m_°c_rolling_1_hours_for_30_min  \
110495                                          7.75   
110496                                          7.50   
110497                                          7.10   
110498                                          6.70   
110499                                          6.45   

        temperature_2m_°c_rolling_std_1_hours_for_30_min  \
110495                                          0.353553   
110496                                          0.000000   
110497                                          0.565685   
110498                                          0.000000   
110499                                          0.353553   

        temperature_2m_°c_rolling_max_1_hours_for_30_min  \
110495                                               8.0   
110496                                               7.5   
110497                                               7.5   
110498                                               6.7   
110499                                               6.7   

        temperature_2m_°c_rolling_min_1_hours_for_30_min  \
110495                                               7.5   
110496                                               7.5   
110497                                               6.7   
110498                                               6.7   
110499                                               6.2   

        relative_humidity_2m_%_rolling_1_hours_for_30_min  \
110495                                               82.5   
110496                                               84.0   
110497                                               86.0   
110498                                               88.0   
110499                                               88.5   

        relative_humidity_2m_%_rolling_std_1_hours_for_30_min  \
110495                                           2.121320       
110496                                           0.000000       
110497                                           2.828427       
110498                                           0.000000       
110499                                           0.707107       

        relative_humidity_2m_%_rolling_max_1_hours_for_30_min  \
110495                                               84.0       
110496                                               84.0       
110497                                               88.0       
110498                                               88.0       
110499                                               89.0       

        relative_humidity_2m_%_rolling_min_1_hours_for_30_min  \
110495                                               81.0       
110496                                               84.0       
110497                                               84.0       
110498                                               88.0       
110499                                               88.0       

        apparent_temperature_°c_rolling_1_hours_for_30_min  \
110495                                               4.40    
110496                                               4.10    
110497                                               3.60    
110498                                               3.10    
110499                                               2.95    

        apparent_temperature_°c_rolling_std_1_hours_for_30_min  \
110495                                           0.424264        
110496                                           0.000000        
110497                                           0.707107        
110498                                           0.000000        
110499                                           0.212132        

      

In [122]:
ck.check(weather_uk_shifted_for_ml_dict["30_min"])

Number of columns: 1427 and rows: 92979

Data types:
settlement_date                                         datetime64[ns]
settlement_period                                                int32
temperature_2m_°c_rolling_1_hours_for_30_min                   float64
temperature_2m_°c_rolling_std_1_hours_for_30_min               float64
temperature_2m_°c_rolling_max_1_hours_for_30_min               float64
                                                             ...      
direct_radiation_w/m²_lag_1_years_for_30_min                   float64
terrestrial_radiation_w/m²_lag_1_years_for_30_min              float64
shortwave_radiation_w/m²_lag_1_years_for_30_min                float64
direct_normal_irradiance_w/m²_lag_1_years_for_30_min           float64
diffuse_radiation_w/m²_lag_1_years_for_30_min                  float64
Length: 1427, dtype: object

Unique values count:
settlement_date                                          1938
settlement_period                                     

### Merging

In [123]:
# Merging the dataframes and saving CSV files by key
for key in uk_demand_merge_updated_for_ml_dict:
    df1 = uk_demand_merge_updated_for_ml_dict[key]
    df2 = carbon_uk_shifted_for_ml_dict[key]
    df3 = weather_uk_shifted_for_ml_dict[key]

    merged = df1.merge(df2, on=["settlement_date", "settlement_period"], how="left")
    merged = merged.merge(df3, on=["settlement_date", "settlement_period"], how="left")

    # Count NaNs before dropping
    nan_rows = merged.isna().any(axis=1).sum()

    # Drop NaNs
    merged_cleaned = merged.dropna()
    print(f"Key '{key}': Dropped {nan_rows} rows with NaNs.")

    # Save to CSV
    merged_cleaned.to_csv(os.path.join(ml_path, f"{key}_merged.csv"), index=False)
    print(f"Key '{key}': Data saved to {key}_merged.csv")

    uk_demand_merge_updated_for_ml_dict[key] = 0


Key '30_min': Dropped 0 rows with NaNs.
Key '30_min': Data saved to 30_min_merged.csv
Key '1_hour': Dropped 0 rows with NaNs.
Key '1_hour': Data saved to 1_hour_merged.csv
Key '2 hour': Dropped 0 rows with NaNs.
Key '2 hour': Data saved to 2 hour_merged.csv
Key '3_hours': Dropped 0 rows with NaNs.
Key '3_hours': Data saved to 3_hours_merged.csv
Key '6_hours': Dropped 0 rows with NaNs.
Key '6_hours': Data saved to 6_hours_merged.csv
Key '12_hours': Dropped 0 rows with NaNs.
Key '12_hours': Data saved to 12_hours_merged.csv
Key '1_day': Dropped 0 rows with NaNs.
Key '1_day': Data saved to 1_day_merged.csv
Key '2_day': Dropped 0 rows with NaNs.
Key '2_day': Data saved to 2_day_merged.csv
Key '3_days': Dropped 0 rows with NaNs.
Key '3_days': Data saved to 3_days_merged.csv
Key '5_days': Dropped 0 rows with NaNs.
Key '5_days': Data saved to 5_days_merged.csv
Key '1_week': Dropped 0 rows with NaNs.
Key '1_week': Data saved to 1_week_merged.csv
Key '2_week': Dropped 0 rows with NaNs.
Key '2_w